In [1]:
import pyspark.sql.functions as F
import pyspark.sql.types as st
from sklearn import preprocessing
import pandas as pd
from numpy import array
import matplotlib.pyplot as plt

### Prepare data

In [3]:
#Global variables
sample_id = 42
week_1_start = '20180923'
week_1_end = '20180929'
week_4_end = '20181020'
week_12_end = '20181215'
week_16_end = '20190112'
day_1_date = '20180925'

In [4]:
ms_1week_raw = spark.sql("""
    SELECT
        client_id,
        coalesce(scalar_parent_browser_engagement_total_uri_count, 0) AS uri_count,
        coalesce(scalar_parent_browser_engagement_active_ticks, 0) AS active_ticks,
        (coalesce(scalar_parent_browser_engagement_active_ticks, 0))*5/3600 AS active_tick_hrs,        
        subsession_length,
        (subsession_length/3600) AS subsession_hours,
        session_length,
        profile_subsession_counter,
        submission_date_s3,
        session_start_date,
        subsession_start_date,
        reason,
        active_addons_count,
        scalar_parent_browser_engagement_max_concurrent_tab_count AS tab_count,
        scalar_parent_browser_engagement_max_concurrent_window_count AS window_count,
        scalar_parent_browser_engagement_unique_domains_count AS domains_count,
        profile_creation_date,
        profile_reset_date,
        previous_build_id,
        normalized_channel,
        os,
        normalized_os_version,
        windows_build_number,
        install_year,
        creation_date,
        distribution_id,
        submission_date,
        app_build_id,
        app_display_version,
        update_channel,
        update_enabled,
        update_auto_download,
        active_experiment_branch,
        timezone_offset,
        vendor,
        is_default_browser,
        default_search_engine,
        client_submission_date,
        places_bookmarks_count,
        places_pages_count,
        scalar_content_telemetry_event_counts AS telem_event_counts,
        scalar_parent_browser_engagement_tab_open_event_count AS tab_event_count,
        scalar_parent_browser_engagement_window_open_event_count AS window_event_count,
        scalar_parent_browser_errors_collected_count AS errors_collected_count,
        scalar_parent_devtools_current_theme AS current_theme,
        scalar_parent_formautofill_availability AS formautofill_availability,
        scalar_parent_media_page_count AS media_page_count, 
        country,
        city,
        geo_subdivision1,
        locale,
        antivirus,
        antispyware,
        firewall,
        session_id,
        subsession_id,
        sync_configured,
        sync_count_desktop,
        sync_count_mobile,
        disabled_addons_ids,
        active_theme,
        user_prefs,
        experiments,
        sample_id,
        document_id
    FROM main_summary
    WHERE 
        app_name='Firefox'
        AND submission_date_s3 >= '{}'
        AND submission_date_s3 <= '{}'
        AND sample_id = '{}'
    ORDER BY
        client_id,
        submission_date_s3,
        profile_subsession_counter
    """.format(week_1_start, week_1_end, sample_id)
    )

search_wk = spark.sql("""
  SELECT
      client_id,
      submission_date_s3,
      engine,
      SUM(sap) as sap,
      SUM(tagged_sap) as tagged_sap,
      SUM(tagged_follow_on) as tagged_follow_on,
      SUM(organic) as in_content_organic
  FROM search_clients_daily
  WHERE
      submission_date_s3 >= '{}'
      AND submission_date_s3 <= '{}'
      AND sample_id = '{}'
  GROUP BY
      1, 2, 3
    """.format(week_1_start, week_1_end, sample_id)
    )

ms_1day_raw = spark.sql("""
    SELECT
        client_id,
        coalesce(scalar_parent_browser_engagement_total_uri_count, 0) AS uri_count,
        coalesce(scalar_parent_browser_engagement_active_ticks, 0) AS active_ticks,
        (coalesce(scalar_parent_browser_engagement_active_ticks, 0))*5/3600 AS active_tick_hrs,        
        subsession_length,
        (subsession_length/3600) AS subsession_hours,
        session_length,
        profile_subsession_counter,
        submission_date_s3,
        session_start_date,
        subsession_start_date,
        subsession_counter,
        reason,
        active_addons_count,
        scalar_parent_browser_engagement_max_concurrent_tab_count AS tab_count,
        scalar_parent_browser_engagement_max_concurrent_window_count AS window_count,
        scalar_parent_browser_engagement_unique_domains_count AS domains_count,
        profile_creation_date,
        profile_reset_date,
        previous_build_id,
        normalized_channel,
        os,
        normalized_os_version,
        windows_build_number,
        install_year,
        creation_date,
        distribution_id,
        submission_date,
        app_build_id,
        app_display_version,
        update_channel,
        update_enabled,
        update_auto_download,
        active_experiment_branch,
        timezone_offset,
        vendor,
        is_default_browser,
        default_search_engine,
        client_submission_date,
        places_bookmarks_count,
        places_pages_count,
        scalar_content_telemetry_event_counts AS telem_event_counts,
        scalar_parent_browser_engagement_tab_open_event_count AS tab_event_count,
        scalar_parent_browser_engagement_window_open_event_count AS window_event_count,
        scalar_parent_browser_errors_collected_count AS errors_collected_count,
        scalar_parent_devtools_current_theme AS current_theme,
        scalar_parent_formautofill_availability AS formautofill_availability,
        scalar_parent_media_page_count AS media_page_count, 
        country,
        city,
        geo_subdivision1,
        locale,
        antivirus,
        antispyware,
        firewall,
        session_id,
        subsession_id,
        sync_configured,
        sync_count_desktop,
        sync_count_mobile,
        disabled_addons_ids,
        active_theme,
        user_prefs,
        experiments,
        sample_id,
        document_id
    FROM main_summary
    WHERE 
        app_name='Firefox'
        AND submission_date_s3 == '{}'
        AND sample_id = '{}'
    ORDER BY
        client_id,
        profile_subsession_counter
    """.format(day_1_date, sample_id)
    )

ms_1day_sum = spark.sql("""
    SELECT 
        client_id,
        submission_date_s3,
        sum(coalesce(scalar_parent_browser_engagement_total_uri_count, 0)) AS td_uri,
        sum(coalesce(scalar_parent_browser_engagement_active_ticks, 0)) AS td_active_ticks,
        sum(coalesce(scalar_parent_browser_engagement_active_ticks, 0)*5/3600) AS td_active_tick_hrs,
        sum(subsession_length/3600) AS td_subsession_hours
    FROM main_summary
    WHERE 
        app_name='Firefox'
        AND submission_date_s3 == '{}'
        AND sample_id = '{}'
    GROUP BY
        1, 2
    """.format(day_1_date, sample_id)
    )

search_day = spark.sql("""
  SELECT client_id,
      submission_date_s3,
      engine,
      SUM(sap) as sap,
      SUM(tagged_sap) as tagged_sap,
      SUM(tagged_follow_on) as tagged_follow_on,
      SUM(organic) as in_content_organic
  FROM search_clients_daily
  WHERE
      submission_date_s3 == '{}'
      AND sample_id = '{}'
  GROUP BY
      1, 2, 3
    """.format(day_1_date, sample_id)
    )

ms_4week_raw = spark.sql("""
    SELECT
        client_id,
        coalesce(scalar_parent_browser_engagement_total_uri_count, 0) AS uri_count,
        coalesce(scalar_parent_browser_engagement_active_ticks, 0) AS active_ticks,
        (coalesce(scalar_parent_browser_engagement_active_ticks, 0))*5/3600 AS active_tick_hrs,        
        subsession_length,
        (subsession_length/3600) AS subsession_hours,
        session_length,
        profile_subsession_counter,
        submission_date_s3,
        session_start_date,
        subsession_start_date,
        reason,
        active_addons_count,
        scalar_parent_browser_engagement_max_concurrent_tab_count AS tab_count,
        scalar_parent_browser_engagement_max_concurrent_window_count AS window_count,
        scalar_parent_browser_engagement_unique_domains_count AS domains_count,
        profile_creation_date,
        profile_reset_date,
        previous_build_id,
        normalized_channel,
        os,
        normalized_os_version,
        windows_build_number,
        install_year,
        creation_date,
        distribution_id,
        submission_date,
        app_build_id,
        app_display_version,
        update_channel,
        update_enabled,
        update_auto_download,
        active_experiment_branch,
        timezone_offset,
        vendor,
        is_default_browser,
        default_search_engine,
        client_submission_date,
        places_bookmarks_count,
        places_pages_count,
        scalar_content_telemetry_event_counts AS telem_event_counts,
        scalar_parent_browser_engagement_tab_open_event_count AS tab_event_count,
        scalar_parent_browser_engagement_window_open_event_count AS window_event_count,
        scalar_parent_browser_errors_collected_count AS errors_collected_count,
        scalar_parent_devtools_current_theme AS current_theme,
        scalar_parent_formautofill_availability AS formautofill_availability,
        scalar_parent_media_page_count AS media_page_count, 
        country,
        city,
        geo_subdivision1,
        locale,
        antivirus,
        antispyware,
        firewall,
        session_id,
        subsession_id,
        sync_configured,
        sync_count_desktop,
        sync_count_mobile,
        disabled_addons_ids,
        active_theme,
        user_prefs,
        experiments,
        sample_id,
        document_id
    FROM main_summary
    WHERE 
        app_name='Firefox'
        AND submission_date_s3 >= '{}'
        AND submission_date_s3 <= '{}'
        AND sample_id = '{}'
    ORDER BY
        client_id,
        submission_date_s3,
        profile_subsession_counter
    """.format(week_1_start, week_4_end, sample_id)
    )

ms_12week_raw = spark.sql("""
    SELECT
        client_id,
        coalesce(scalar_parent_browser_engagement_total_uri_count, 0) AS uri_count,
        coalesce(scalar_parent_browser_engagement_active_ticks, 0) AS active_ticks,
        (coalesce(scalar_parent_browser_engagement_active_ticks, 0))*5/3600 AS active_tick_hrs,        
        subsession_length,
        (subsession_length/3600) AS subsession_hours,
        session_length,
        profile_subsession_counter,
        submission_date_s3,
        session_start_date,
        subsession_start_date,
        reason
    FROM main_summary
    WHERE 
        app_name='Firefox'
        AND submission_date_s3 >= '{}'
        AND submission_date_s3 <= '{}'
        AND sample_id = '{}'
    ORDER BY
        client_id,
        submission_date_s3,
        profile_subsession_counter
    """.format(week_1_start, week_12_end, sample_id)
    )


In [5]:
# Look at the summary stats for raw ping values over a day
display(ms_1day_raw['uri_count', 'active_ticks', 'active_tick_hrs', 'subsession_length', 'subsession_hours', 'submission_date_s3'].describe())

summary uri_count active_ticks active_tick_hrs subsession_length subsession_hours submission_date_s3 count 3982350 3982350 3982350 3982347 3982347 3982350 mean 34.62774869109948 121.61577159215037 0.1689107938779816 8361.558932709782 2.322655259086069 2.0180925E7 stddev 1150.5542265691665 302.4990749648113 0.42013760411779366 96004.72059727825 26.667977943688342 0.0 min 0 0 0.0 0 0.0 20180925 max 1350738 17273 23.990277777777777 88352282 24542.300555555557 20180925

From search_clients_daily, group by day then add sap and in_content_organic for total daily search counts.  
Then join with the table of other count values summed over 1 day.

In [7]:
# Replace the null values with 0s
search_day = search_day.na.fill(0)
# Sum over the day
search_day_sum = search_day.groupBy("client_id", "submission_date_s3") \
                           .agg(F.sum(F.col("sap")+F.col("in_content_organic")))  \
                           .withColumnRenamed('sum((sap + in_content_organic))','td_search_counts')
# Join the daily search counts with the other daily counts 
ms_1day = ms_1day_sum.join(search_day_sum, ['client_id', 'submission_date_s3'], 'full_outer').na.fill(0)
display(ms_1day['submission_date_s3', 'td_uri', 'td_active_ticks', 'td_active_tick_hrs', 'td_subsession_hours'])

submission_date_s3 td_uri td_active_ticks td_active_tick_hrs td_subsession_hours 20180925 27 59 0.08194444444444444 23.99888888888889 20180925 17 137 0.19027777777777777 0.43944444444444447 20180925 0 180 0.25 0.3144444444444444 20180925 32 0 0.0 4.384444444444445 20180925 835 2039 2.8319444444444444 4.078055555555555 20180925 0 3308 4.594444444444444 40.18472222222222 20180925 3 29 0.04027777777777778 0.6077777777777778 20180925 9 0 0.0 1.9880555555555555 20180925 0 0 0.0 2.7413888888888884 20180925 53 416 0.5777777777777777 2.557777777777778 20180925 44 76 0.10555555555555556 25.995555555555555 20180925 13 160 0.2222222222222222 41.59444444444445 20180925 44 319 0.4430555555555556 1.4811111111111113 20180925 0 0 0.0 1.0225 20180925 69 199 0.2763888888888889 1.5444444444444445 20180925 4 16 0.02222222222222222 2.808888888888889 20180925 146 1271 1.765277777777778 4.744722222222222 20180925 130 358 0.49722222222222223 1.6997222222222221 20180925 40 153 0.2125 1.0469444444444445 20180925 0 629 0.8736111111111111 1.5583333333333333 20180925 0 0 0.0 24.0 20180925 453 1211 1.6819444444444445 2.451944444444445 20180925 119 325 0.4513888888888889 5.060555555555555 20180925 564 1178 1.6361111111111113 18.343611111111112 20180925 299 299 0.41527777777777775 0.4608333333333333 20180925 120 399 0.5541666666666667 2.047777777777778 20180925 0 2 0.002777777777777778 0.0019444444444444444 20180925 5 49 0.06805555555555555 4.3225 20180925 8 300 0.4166666666666667 25.491944444444446 20180925 21 60 0.08333333333333333 1.4958333333333333 20180925 2 410 0.5694444444444444 5.596388888888889 20180925 13 34 0.04722222222222222 7.316388888888889 20180925 195 617 0.8569444444444445 4.0569444444444445 20180925 4 12 0.016666666666666666 0.020277777777777777 20180925 1 8 0.011111111111111112 0.06916666666666667 20180925 0 0 0.0 15.334722222222222 20180925 528 1744 2.4222222222222216 454.3752777777778 20180925 8 165 0.22916666666666666 5.966388888888889 20180925 191 657 0.9125000000000001 3.396111111111111 20180925 0 48 0.06666666666666667 0.2652777777777778 20180925 78 171 0.2375 24.18888888888889 20180925 8 19 0.026388888888888892 0.20194444444444445 20180925 3 45 0.0625 3.9525 20180925 71 193 0.26805555555555555 2.8141666666666665 20180925 74 738 1.025 3.0394444444444444 20180925 178 714 0.9916666666666666 3.9552777777777774 20180925 83 163 0.2263888888888889 3.5141666666666667 20180925 217 516 0.7166666666666667 2.213888888888889 20180925 0 1 0.001388888888888889 5.555555555555556E-4 20180925 19 98 0.13611111111111113 0.1463888888888889 20180925 83 180 0.25 1.5097222222222224 20180925 5 22 0.030555555555555555 0.3741666666666667 20180925 170 712 0.9888888888888888 21.951666666666668 20180925 26 113 0.15694444444444444 0.5208333333333334 20180925 15 0 0.0 1.2455555555555555 20180925 99 776 1.0777777777777777 5.438055555555556 20180925 203 0 0.0 10.761666666666667 20180925 210 825 1.1458333333333335 2.5405555555555557 20180925 0 96 0.13333333333333333 0.6072222222222222 20180925 56 352 0.4888888888888889 2.229722222222222 20180925 168 1305 1.8125 16.775 20180925 453 1417 1.9680555555555554 23.99972222222222 20180925 17 69 0.09583333333333333 0.17416666666666666 20180925 95 462 0.6416666666666667 13.413055555555555 20180925 7 65 0.09027777777777778 8.98611111111111 20180925 54 246 0.3416666666666667 23.997222222222224 20180925 0 5 0.006944444444444444 18.514166666666668 20180925 26 106 0.14722222222222223 0.27472222222222226 20180925 115 667 0.9263888888888889 23.99972222222222 20180925 255 534 0.7416666666666666 7.4094444444444445 20180925 35 148 0.20555555555555555 25.802222222222223 20180925 173 0 0.0 13.955 20180925 27 109 0.15138888888888888 0.9499999999999998 20180925 0 43 0.059722222222222225 0.1413888888888889 20180925 45 96 0.13333333333333333 4.059166666666667 20180925 5 28 0.03888888888888889 23.985277777777778 20180925 2 26 0.03611111111111111 24.00027777777778 20180925 26 55 0.0763888888888889 0.44555555555555554 20180925 0 3 0.00416666666

In [8]:
# Sanity check
display(search_day_sum)

client_id submission_date_s3 td_search_counts 4a13d30a-930d-034e-bcab-de3449b2fc8e 20180925 17 699695bd-df46-4fd9-9fb1-c71f642fff10 20180925 2 e5349fda-db9c-4df4-a374-b249d3dea8c5 20180925 5 454c153e-0b05-4d7a-a21d-f9dcfe8a6e70 20180925 1 082781f4-0534-460a-9b83-dfbd3fa142f7 20180925 89 e7d01afc-b68b-4eb8-a16c-9397c966288a 20180925 1 f8fe6acc-7b16-42cc-9162-836119fdfa58 20180925 3 aa1ac09b-8f6d-45cd-83d7-21b31268230b 20180925 2 07640daf-0a0b-434a-98af-54ef626ebf79 20180925 5 d9934e49-a258-4a2b-8df5-042d0f0cb169 20180925 1 e6085dfd-4fde-47c9-a6d6-f1ae68a1139d 20180925 1 6563f54f-68c3-463e-8b18-77c6012d0833 20180925 1 eae6df2f-c40e-4c68-8133-26027f20f4e3 20180925 2 35eb53a7-23a6-4457-90b0-98846b5ee62a 20180925 9 20d38a61-2aaf-4843-9241-c1ccfb083cdc 20180925 8 ec203059-496a-4e4c-b54f-972ae54d4782 20180925 1 efe1cdcb-c5ea-4b83-b4ab-677803cd8a5a 20180925 8 c1a2c333-af25-b04e-97bf-3bacf4865038 20180925 1 7c179c1e-bbf3-49d3-8c51-c1545f1cb3a6 20180925 1 6ae5b486-53b3-4b46-aba0-8181e883ace8 20180925 2 f550cd3b-aad1-4e7b-b3cf-32b6c1cc7bff 20180925 1 0f8e0cc9-9337-4e21-9ffc-2a59a9c88c44 20180925 6 fb872b48-7411-4647-b1a7-688446ed6362 20180925 9 49aa2bf1-0ffe-4d2d-9a13-fb2b245e8e78 20180925 5 22a7c2de-f814-4bda-a4c4-071fcbb8ee3f 20180925 1 ebc9bcea-4bae-4dcb-8bdc-e5a7dfea2fd5 20180925 13 fbb82d5a-5629-41c5-a24a-5a365c815c4d 20180925 2 1f466e27-5dfa-450f-b512-c8f47d807492 20180925 1 e62303a7-111c-4e60-8d15-5c65f4f08374 20180925 2 b1eedb7d-b11b-4f9d-853f-7b593213d2e4 20180925 9 7cbece23-95cc-42ab-af51-f478aa0d0a08 20180925 1 c161df71-2376-4f80-803e-f1d7fd1435df 20180925 5 90c2ceb4-2290-4b4f-9b99-d029d064cc0b 20180925 4 63b279b7-4f8c-294e-bbef-b88e910eda76 20180925 3 ffa515e2-759c-4c8c-9ae6-edee3e8b8f5c 20180925 26 cacc0614-96fc-4dd3-824d-f263c95c1fd3 20180925 1 b3c84ad8-e4a6-4163-b0da-94fa335cd0ba 20180925 3 4dcb6e83-3133-4329-9ccc-bd47808c1522 20180925 1 501092b8-7a5a-4e9f-8b51-2e2caeecc9e6 20180925 10 70d8374e-d1e8-49b0-9364-36f456c7ca54 20180925 2 871d5ce8-2337-4c47-a917-00a8b3397a2f 20180925 4 3e7e5e2f-520c-8c46-b25c-74ffc1fdfad2 20180925 11 041a1f2c-52e0-4038-9deb-dba266596d5f 20180925 1 1da071ab-a1fa-4e63-b99a-1587b8c2bbfc 20180925 1 87521c0c-ed01-4041-9821-f8e3e4ccc4a5 20180925 2 b19c2422-96ad-4ff6-ac27-0948faf76cf1 20180925 1 e0a8e136-2b6e-4fee-a74a-f88a0df1a432 20180925 1 bf191b8e-1582-4fef-b339-452c19c0e5f1 20180925 7 08dbac8d-b376-4e72-9102-195c6b0ff2c3 20180925 3 c8799a61-8332-4949-a74e-745a7a5b6ff5 20180925 1 ea54794b-3d39-4fc9-ba37-b1f5fd29f0b9 20180925 1 3c821745-08d7-4faf-90e8-e07c5df9bebc 20180925 3 2561a3c1-abd4-4496-821a-fc11147fdb8e 20180925 3 0e10eb39-8ec6-4ba4-a440-85d1f78bfd19 20180925 1 933676cc-29f7-445a-b5e9-38e0b91e6676 20180925 0 03970b89-821c-4202-8384-1643a447a72a 20180925 12 2ccc36a0-9f25-4b86-99e2-2bdcf4453803 20180925 1 b98779d1-c20a-45c0-9335-1a2619c1adcb 20180925 1 278afb3e-9448-43d1-9d98-159276233033 20180925 1 1e9fd087-12ff-40a9-892a-9921a4428377 20180925 2 dbbf02d4-f505-4bb5-b6e9-cb34f13b9243 20180925 1 a95c179e-f0a7-400c-8708-5e1cb9bc0ac8 20180925 1 cb7968c2-0a51-4389-8be8-7cdb3aeee839 20180925 7 0de7c17d-3ce4-4edc-aae0-bd1c632f7edf 20180925 2 ea039b7d-8d8f-400f-b5a5-cae43a700bab 20180925 3 507623b4-f753-f848-981f-8dbadd48c5e6 20180925 7 f90e325e-9ff6-486a-b3ef-585437875fff 20180925 17 febdc5ed-5d65-794a-b946-4be06b927c9c 20180925 10 55094bb1-2d50-43a7-bca5-ad0a70df02a0 20180925 11 6b531833-55f4-400a-96ff-688be622f39c 20180925 8 cf57a28c-6e79-a54f-b184-f97569896283 20180925 10 6edced1e-a740-4f8b-a0d9-d7edad283747 20180925 1 b329c55d-914e-4469-98da-1ed345021f50 20180925 1 0d97bd92-06c1-47dd-93c7-2ac8f3664c9b 20180925 1 bdda81ab-2aac-4f83-af9b-baef07bc4c54 20180925 1 20841240-c90b-1648-82de-5a7a0d0794d1 20180925 2 9ac211d8-8f56-4b86-b29c-fb87bbaf8998 20180925 2 b4373d44-e20b-44f9-bfbc-bb0f168733d0 20180925 4 29f06004-344e-4014-a21e-894b348a2783 20180925 2 d742f17e-4b10-41f2-8c3f-1d31014e4fd8 20180925 4 ae6e13e1-62ae-4e45-9547-d77aafb3cc6d 20180925 1 cebb4bee-2f41-4338-94af-a1dc4d309303 20180925 2 36df1be

In [9]:
# Look at the raw ping values over a week
display(ms_1week_raw['uri_count', 'active_ticks', 'active_tick_hrs', 'subsession_length', 'subsession_hours', 'submission_date_s3'].describe())

summary uri_count active_ticks active_tick_hrs subsession_length subsession_hours submission_date_s3 count 24422216 24422216 24422216 24422210 24422210 24422216 mean 33.219191084052326 122.21067768788876 0.16973705234433262 9287.209083903545 2.5797803010843143 2.018092597876589E7 stddev 584.7499534626065 305.2711510127229 0.42398770973989236 1519582.398768823 422.1062218802276 1.8711158013718243 min 0 0 0.0 0 0.0 20180923 max 1350738 51622 71.69722222222222 5674255761 1576182.1558333333 20180929

From search_clients_daily, group by date then add sap and in_content_organic for total daily search counts.  
Then join with the table of other count values summed over 1 day.

In [11]:
# Replace the null values with 0s
search_wk = search_wk.na.fill(0)
# Sum over the day
search_wk_sum = search_wk.groupBy("client_id", "submission_date_s3") \
                         .agg(F.sum(F.col("sap")+F.col("in_content_organic"))) \
                         .withColumnRenamed('sum((sap + in_content_organic))','search_counts')
#search_wk_sum.describe().show()
# Note - this isn't joined with week values because we don't have week values summed by day

In [12]:
# Sanity check
display(search_wk_sum)

client_id submission_date_s3 search_counts 5250e883-8518-4042-8b8b-3aa0543abd41 20180928 1 6daccc97-5f4f-4524-b36d-6967aa9306f1 20180928 16 d47777fd-1503-469a-b690-9e1eafc2e5d5 20180928 10 d7d24467-b755-4153-95c4-7d7bb1937a4b 20180928 2 c9ae4e47-dbed-4f60-bc28-3a6830300dfd 20180928 10 7410d83d-4f6b-401f-8f3a-30f9bbe0b290 20180928 3 ac0c7a0f-63af-4d38-ae79-332138c90b87 20180928 4 183aef64-52c5-4e51-b6b2-93eb52191f2a 20180928 10 80b38fe7-0aa3-4310-ac8d-b4769eb43d3b 20180928 2 eb2ab057-7ba4-4ce0-8602-3295ce39f89a 20180928 1 b98b0b36-c564-42c3-ac95-f32d86b0d7bc 20180928 1 9f39ba13-bd4b-4f97-87b8-b74f40571780 20180928 1 64d92c5b-1da7-4727-bf68-c80a3c373a79 20180928 4 37f60038-d940-438c-b0c2-713f229d6d3c 20180928 1 0c7bc93e-2a25-4f4a-9569-cb68e39feaa3 20180928 6 d75317c8-602c-4444-be03-5903f0f37bb4 20180928 6 d2809f3c-cc1d-4cf6-9f9b-422632ed6353 20180928 0 d957047f-4368-420d-8c7d-d2d5479732ad 20180928 2 f1acf0fb-b10a-0b4d-a699-46ff4b709c1d 20180928 63 986e8921-78ac-4cd3-aaa8-6836a70ae161 20180928 8 3036e7bf-583f-4101-ab53-36034c634493 20180928 1 0bf1865f-b511-4aa3-8fe4-334f7d9ba538 20180928 60 48ac1b48-5032-442c-a97c-34c3d5f9cc8b 20180928 44 69901ca4-1d4a-4c37-8d75-3e26e0c54fcf 20180928 1 5472b4fb-5558-4bd5-be22-a88679d21a8f 20180925 10 95e3566a-8a27-4d84-b524-8b2888c477d5 20180925 3 a8cb7436-5575-46eb-a9c2-0ef416ad81ef 20180925 3 d76a5201-464b-47f3-8c0e-4e5ad81e55d7 20180925 26 f20fd5e3-2c19-ea4b-92b7-77e9625081c3 20180925 2 404b6078-d494-4a4f-bfd5-ef1b22d5c549 20180925 2 b378b6a7-7155-4c15-99c8-d0853279fe5e 20180925 13 84bd1ff5-d896-4c2f-bee4-b5fd0c5312c2 20180925 5 a88437cd-0ddf-5c4a-b5c2-fe51dc85d2cb 20180925 8 3aeb5a76-5ade-4db6-bf4c-78649f55c6f7 20180925 3 5168342d-6472-4cd8-b294-3bf3cfc35a90 20180925 21 3a9a0c5f-3416-4e5e-879a-93ac22d71301 20180925 1 e0681069-7c8e-4581-b434-62adbc66a110 20180925 1 945457c1-2ca1-4e22-9be7-86ebce809b09 20180925 11 545ad5c6-c736-42f4-aefa-bb9002977b2c 20180925 17 92070608-303b-4823-8af4-d4357a7fa68d 20180925 3 c95b58f9-7d22-4657-b3e6-bef2198df992 20180925 2 238e65bb-e2cc-bb42-9e3a-7089d7bc9085 20180925 30 b93137ce-a20a-4c03-b80c-2ad3d76b3251 20180925 2 7ef019b0-8a2c-4d54-83f9-cf72094a6c29 20180925 7 eea102b5-7002-4bf0-8bb8-1421997be732 20180925 3 d3971969-f111-4617-a7fe-36b9f892e609 20180925 11 1756c0dc-2551-4aca-b62e-5036c6709bb9 20180925 1 3df551ef-077e-409d-882f-186d15973af0 20180929 1 1e632208-859e-4ca7-a788-9f8e0c029a8c 20180929 1 585065e8-6f2b-4dfa-86c3-7abcd330c69e 20180929 2 a59cd31f-9366-4516-90e0-49608a94ff31 20180929 2 06c7d959-7243-4f28-a834-bbae0b1e1a2c 20180929 4 ab5cba10-1f75-425b-acd8-75ac25ec91a5 20180929 1 f58f6c79-1c5c-4458-a9e5-e7b5497fb856 20180929 1 250b34c7-101b-4424-b4e2-76655e8b47d4 20180929 4 a8c69133-501a-4d4b-aa6c-55b814d3092d 20180923 3 21a468dc-82e7-475f-a6e0-231f2ff3eb17 20180923 20 5216875c-42c1-490f-97ae-21c15a3d8dab 20180923 13 24f67ba5-d72d-4177-8815-e990ed62a5a8 20180923 2 9f5070af-00a4-43d6-8aa1-6372c061e19f 20180923 15 53a85940-7989-45af-8d27-0007442fe937 20180923 5 6c796a5f-13b6-4244-9116-7735eb66a52e 20180923 1 9a028c0f-f58a-4f66-9bd1-760c0dc969ad 20180923 1 9746977d-595c-4e9b-87d3-9850750fce92 20180923 24 f274ca06-8d63-4cc7-bedd-926cabb58a62 20180924 3 55ce246f-6e5a-4b1f-94c4-b0d674d2d91a 20180924 4 6364d69c-26cd-6449-bad0-b7b8d095abcc 20180924 46 e8663876-d4ed-bd48-aed9-9d1d15dadf4c 20180924 4 ef352980-fe0f-448b-843e-9dff77fd71fe 20180924 29 d53299f5-4731-472f-b585-57c7416140ef 20180924 0 006aabe2-0d02-4333-9281-ad5f0fbb8777 20180924 7 86915112-2d17-447a-8fa8-024cfb18b271 20180924 1 5757984b-4120-47c6-ad75-477ea7f0b7d3 20180924 11 ffa6382d-22b6-4701-9210-63461f93d5b9 20180924 2 334aac1a-dd67-49fb-80d6-ef382a30b722 20180924 1 3e601b0e-6bca-4286-96fb-4c5317c0572c 20180924 4 7704215b-0023-43a9-93d0-a6b4814e4c1f 20180926 3 993a41a4-64c0-469e-8d57-4d4524855050 20180926 1 caebb2bf-312f-4ef8-b394-6237f595a449 20180926 33 3db9f501-8df5-4144-9336-0a5a55f9bbb9 20180926 6 6eabe36c-92a3-4835-b429-8f791e391028 20180926 1 e61042bc-0404-4487-bc2a-19d162adae29 20180926 

####Start looking at some specific cases to determine if they are invalid or show us something interesting about usage.

In [14]:
# How many 1 day ping records with uri_count of zero
ms_1day_0uri = ms_1day_raw.filter(F.col("uri_count") == 0)
ms_1day_0uri.count()

Out[ 114 ]: 1297180

In [15]:
# How many 1 day ping records with active ticks of zero
ms_1day_0at = ms_1day_raw.filter(F.col("active_ticks") == 0)
ms_1day_0at.count()

Out[ 115 ]: 1052848

####Lots of pings with 0 uri and 0 active ticks.

In [17]:
# How many 1 day ping records with both uri and active tick of 0
ms_1day_p_0uriat = ms_1day_raw.filter((F.col("uri_count") == 0) & (F.col("active_ticks") == 0))
ms_1day_p_0uriat.count()

Out[ 116 ]: 796162

In [18]:
ms_1day_raw_cols = ms_1day_raw.columns
ms_1day_raw_cols.remove('client_id')

In [19]:
# Look at pings with 0 uri and 0 active ticks
display(ms_1day_p_0uriat.select(ms_1day_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date subsession_counter reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 0 0 0.0 31 0.008611111111111111 31179 1203 20180925 2018-09-24T20:00:00.0-04:00 2018-09-25T05:00:00.0-04:00 2 aborted-session 17 1 1 null 17507 null null release Windows_NT 10.0 17134 2018 2018-09-25T09:17:45.417Z null 20180925 20180920131237 62.0.2 release true true null -240 Mozilla true other-Norton Safe Search Tue, 25 Sep 2018 09:23:58 GMT null null null null null null null null null US Bradenton FL en-US List(Norton Security) null List(Norton Security) 3fb7f219-7186-455b-904a-b90ff9c61964 3c5fbd0c-4913-43a0-af32-82f7e5b632f6 null 1 0 null List(default-theme@mozilla.org, false, Default, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(searchCohort -> nov17-2) 42 11936f63-7c50-4c64-b7f1-cc456dd9848d 0 0 0.0 24552 6.82 219539 489 20180925 2018-09-07T20:00:00.0-04:00 2018-09-24T08:00:00.0-04:00 16 daily 10 0 0 null 14786 null null release Darwin 17.7.0 null null 2018-09-25T12:25:32.339Z null 20180925 20180807170231 61.0.2 release true true null -240 Mozilla false google-2018 Tue, 25 Sep 2018 12:31:34 GMT null null null null null null null null null US ?? CT en-US null null null 6ae51ad6-ead9-4142-9f24-194fb8ea000b 6aa7fbf5-fbb1-924e-a137-b369514cc52c null null null null List(default-theme@mozilla.org, false, Default, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(rollout-restart-manager-release-1481278 -> active, searchCohort -> nov17-2) 42 24c69e0a-ff26-b744-8d50-6623dbe84523 0 0 0.0 23856 6.626666666666667 73772 2030 20180925 2018-09-24T00:00:00.0+02:00 2018-09-25T00:00:00.0+02:00 2 shutdown 4 2 1 null 15646 null null esr Windows_NT 6.1 null 2012 2018-09-25T04:37:36.195Z null 20180925 20171226003912 52.5.3 esr false false null 120 Mozilla true google Tue, 25 Sep 2018 05:31:09 GMT null null null null null null null null null DE Berlin BE de null null null 5af15575-e311-4461-bc58-1160a3efec38 a3539c4f-5dec-456f-98b8-750dcff39e3c null null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Standard, false, false, 52.5.3, 4, null, false, false, 15636, 17526, null, null, null, null) null null 42 7783e93b-7895-4dd8-8caa-f2d958552740 0 0 0.0 8413 2.3369444444444443 8471 2031 20180925 2018-09-25T00:00:00.0+02:00 2018-09-25T00:00:00.0+02:00 1 shutdown 4 2 1 null 15646 null null esr Windows_NT 6.1 null 2012 2018-09-25T07:50:21.225Z null 20180925 20171226003912 52.5.3 esr false false null 120 Mozilla true google Tue, 25 Sep 2018 11:34:24 GMT 33 32 null 1 null null null null null DE Berlin BE de null null null 7cad490a-718b-4937-9ae8-50e7b1575d2d 74f68f12-47d2-4b81-9aa3-b1a01fa01afb false null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Standard, false, false, 52.5.3, 4, null, false, false, 15636, 17526, null, null, null, null) null null 42 2b1bc204-4335-4b14-9182-88d821cff809 0 0 0.0 86411 24.003055555555555 118683 295 20180925 2018-09-24T00:00:00.0+02:00 2018-09-25T00:00:00.0+02:00 2 daily 4 5 1 null 17463 null null release Wind

In [20]:
# Number of distinct client ids with both 0 uri and 0 active_ticks
ms_1day_p_0uriat.select("client_id").distinct().count()

Out[ 119 ]: 165413

How many fewer clients with both zero counts would there be if the pings were consolidated into days?  
Still a lot

In [22]:
# Number of client records in a day with both uri and active ticks of 0
ms_1day_s_0uriat = ms_1day.filter((F.col("td_uri") == 0) & (F.col("td_active_ticks") == 0))
ms_1day_s_0uriat.count()

Out[ 120 ]: 83621

In [23]:
ms_1day_cols = ms_1day.columns
ms_1day_cols.remove('client_id')
ms_1day_cols.remove('td_search_counts')
# Look at the specific records
display(ms_1day_s_0uriat.select(ms_1day_cols))

submission_date_s3 td_uri td_active_ticks td_active_tick_hrs td_subsession_hours 20180925 0 0 0.0 2.7413888888888884 20180925 0 0 0.0 1.0225 20180925 0 0 0.0 24.0 20180925 0 0 0.0 15.334722222222222 20180925 0 0 0.0 0.04694444444444445 20180925 0 0 0.0 11.468333333333334 20180925 0 0 0.0 5.942222222222222 20180925 0 0 0.0 24.000833333333333 20180925 0 0 0.0 2.3244444444444445 20180925 0 0 0.0 2.7852777777777775 20180925 0 0 0.0 42.373333333333335 20180925 0 0 0.0 18.864444444444445 20180925 0 0 0.0 2.361388888888889 20180925 0 0 0.0 8.009444444444444 20180925 0 0 0.0 23.99972222222222 20180925 0 0 0.0 1.3211111111111111 20180925 0 0 0.0 23.999166666666667 20180925 0 0 0.0 4.127222222222223 20180925 0 0 0.0 23.99972222222222 20180925 0 0 0.0 3.7216666666666667 20180925 0 0 0.0 23.84638888888889 20180925 0 0 0.0 0.0044444444444444444 20180925 0 0 0.0 0.6872222222222222 20180925 0 0 0.0 12.649444444444445 20180925 0 0 0.0 0.041666666666666664 20180925 0 0 0.0 6.834444444444443 20180925 0 0 0.0 4.458055555555556 20180925 0 0 0.0 1.0580555555555555 20180925 0 0 0.0 3.685000000000001 20180925 0 0 0.0 5.641388888888888 20180925 0 0 0.0 23.986944444444443 20180925 0 0 0.0 11.831944444444444 20180925 0 0 0.0 2.8241666666666667 20180925 0 0 0.0 1.2144444444444444 20180925 0 0 0.0 0.09388888888888888 20180925 0 0 0.0 0.06444444444444444 20180925 0 0 0.0 1.9533333333333334 20180925 0 0 0.0 5.668333333333333 20180925 0 0 0.0 0.011666666666666667 20180925 0 0 0.0 7.796666666666666 20180925 0 0 0.0 23.99972222222222 20180925 0 0 0.0 10.104722222222222 20180925 0 0 0.0 0.04777777777777778 20180925 0 0 0.0 8.35888888888889 20180925 0 0 0.0 0.14888888888888888 20180925 0 0 0.0 15.619166666666667 20180925 0 0 0.0 30.05638888888889 20180925 0 0 0.0 8.776388888888889 20180925 0 0 0.0 0.11472222222222223 20180925 0 0 0.0 23.99972222222222 20180925 0 0 0.0 23.99972222222222 20180925 0 0 0.0 0.6897222222222222 20180925 0 0 0.0 23.99972222222222 20180925 0 0 0.0 5.086111111111111 20180925 0 0 0.0 1.676388888888889 20180925 0 0 0.0 9.405277777777778 20180925 0 0 0.0 0.4230555555555556 20180925 0 0 0.0 1.9758333333333333 20180925 0 0 0.0 4.738611111111111 20180925 0 0 0.0 11.592777777777776 20180925 0 0 0.0 7.636388888888889 20180925 0 0 0.0 71.97638888888889 20180925 0 0 0.0 0.25166666666666665 20180925 0 0 0.0 12.650555555555556 20180925 0 0 0.0 0.775 20180925 0 0 0.0 30.337777777777777 20180925 0 0 0.0 0.2861111111111111 20180925 0 0 0.0 0.06194444444444444 20180925 0 0 0.0 24.000555555555554 20180925 0 0 0.0 0.6380555555555556 20180925 0 0 0.0 1.388888888888889 20180925 0 0 0.0 0.20361111111111113 20180925 0 0 0.0 23.99972222222222 20180925 0 0 0.0 3.444444444444444 20180925 0 0 0.0 10.9725 20180925 0 0 0.0 4.995277777777778 20180925 0 0 0.0 1.0088888888888887 20180925 0 0 0.0 23.999444444444446 20180925 0 0 0.0 0.026388888888888885 20180925 0 0 0.0 0.04027777777777778 20180925 0 0 0.0 1.4941666666666666 20180925 0 0 0.0 23.99972222222222 20180925 0 0 0.0 1.6897222222222221 20180925 0 0 0.0 3.8383333333333334 20180925 0 0 0.0 1.121388888888889 20180925 0 0 0.0 1.5072222222222222 20180925 0 0 0.0 24.0 20180925 0 0 0.0 0.4886111111111111 20180925 0 0 0.0 15.250277777777779 20180925 0 0 0.0 10.917777777777777 20180925 0 0 0.0 0.019166666666666665 20180925 0 0 0.0 24.0 20180925 0 0 0.0 0.43472222222222223 20180925 0 0 0.0 1.5372222222222223 20180925 0 0 0.0 24.000555555555554 20180925 0 0 0.0 23.99972222222222 20180925 0 0 0.0 0.13499999999999998 20180925 0 0 0.0 5.47 20180925 0 0 0.0 45.23166666666666 20180925 0 0 0.0 0.026111111111111113 20180925 0 0 0.0 23.99972222222222 20180925 0 0 0.0 15.81611111111111 20180925 0 0 0.0 2.8405555555555555 20180925 0 0 0.0 24.05666666666667 20180925 0 0 0.0 0.015277777777777779 20180925 0 0 0.0 3.2672222222222222 20180925 0 0 0.0 0.0044444444444444444 20180925 0 0 0.0 23.965833333333332 20180925 0 0 0.0 47.503055555555555 20180925 0 0 0.0 14.258888888888889 20180925 0 0 0.0 13.531944444444445 20180925 0 0 0.0 90.436

How many clients with total daily uri >= 5 with 0 active_ticks?  
Greater than 72,000 - Not sure how it is possible to get this usage pattern.

In [25]:
# Number of client records in a day with uri >= 5 and active ticks of 0
ms_1day_s_uri_0at = ms_1day_sum.where("td_uri >= 5 and td_active_ticks = 0")
ms_1day_s_uri_0at.count()

Out[ 122 ]: 72673

Double check 0 uri and active ticks for client e9ec with 32 search count  
Lots of short sessions in 1 day, profile_subsession_counter in order, but no activity

In [27]:
# Look at 1 day's pings for client e9ec
ms_1day_test = ms_1day_raw.filter("client_id like '%6e64dd36e9ec'")
display(ms_1day_test.select(ms_1day_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date subsession_counter reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 0 0 0.0 11199 3.1108333333333333 19625 1172 20180925 2018-09-24T00:00:00.0+01:00 2018-09-25T00:00:00.0+01:00 2 shutdown 7 3 1 null 16565 17356 null esr Windows_NT 6.0 null 2011 2018-09-25T02:11:13.948Z null 20180925 20180621064021 52.9.0 esr true true null 60 Mozilla false google Tue, 25 Sep 2018 02:12:17 GMT null null null 4 null null null null null GB Stockton-on-Tees ENG en-GB null null null 959350a7-4a41-4e00-9c9c-47724de2b856 f84cbb24-991e-461e-b801-e4e3a8947876 null null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Default, false, false, 52.9.0, 4, null, false, false, 17345, 17708, null, null, null, null) null null 42 2790a186-965c-4732-899b-89fec205af55 0 0 0.0 4657 1.293611111111111 4658 1173 20180925 2018-09-25T00:00:00.0+01:00 2018-09-25T00:00:00.0+01:00 1 shutdown 7 3 1 null 16565 17356 null esr Windows_NT 6.0 null 2011 2018-09-25T03:28:54.274Z null 20180925 20180621064021 52.9.0 esr true true null 60 Mozilla false ddg Tue, 25 Sep 2018 03:29:59 GMT null null null 4 null null null null null GB Stockton-on-Tees ENG en-GB null null null 002bdc56-9277-4999-877c-c7bbad4949ca 68a92149-bab8-44ff-abde-dd788c6fde87 false null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Default, false, false, 52.9.0, 4, null, false, false, 17345, 17708, null, null, null, null) null null 42 812f2373-b374-43ec-81b4-6db3c8247530 0 0 0.0 198 0.055 199 1174 20180925 2018-09-25T00:00:00.0+01:00 2018-09-25T00:00:00.0+01:00 1 shutdown 7 1 1 null 16565 17356 null esr Windows_NT 6.0 null 2011 2018-09-25T03:32:18.262Z null 20180925 20180621064021 52.9.0 esr true true null 60 Mozilla false ddg Tue, 25 Sep 2018 15:50:11 GMT null null null null null null null null null GB Middlesbrough ENG en-GB null null null 4b9945db-4b57-4b6a-bf93-f25e0e314da6 4993c0f1-6331-4d66-a70b-0287f9e25730 false null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Default, false, false, 52.9.0, 4, null, false, false, 17345, 17708, null, null, null, null) null null 42 3d4e344c-cdf1-4139-a0c8-17c8f7715d1d 0 0 0.0 40 0.011111111111111112 40 1175 20180925 2018-09-25T00:00:00.0+01:00 2018-09-25T00:00:00.0+01:00 1 shutdown 7 3 1 null 16565 17356 null esr Windows_NT 6.0 null 2011 2018-09-25T03:43:21.280Z null 20180925 20180621064021 52.9.0 esr true true null 60 Mozilla false google Tue, 25 Sep 2018 15:50:11 GMT null null null 3 null null null null null GB Middlesbrough ENG en-GB null null null 954cd7f7-26c0-4b48-a8f5-6dd61a0de0ec 72ba137e-4377-40be-b3d7-b6fce6b5970b false null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Default, false, false, 52.9.0, 4, null, false, false, 17345, 17708, null, null, null, null) null null 42 f4f75c48-5917-4daa-a1a7-618298d38dc4 0 0 0.0 5009 1.3913888888888888 5010 1176 20180925 2018-09-25T00:00:00.0+01:00 2018-09-25T00:00:00.0+01:00 1 environment-change 7 4 1 null 16565 17356 null esr Windows_NT 6.0 null 2011 2018-09-25T17:12:41.352Z null 20180925 20180621064021 52.9.0 es

In [28]:
# Check search counts for the same client as above, e9ec
search_day_test = search_day.filter("client_id like '%6e64dd36e9ec'")
display(search_day_test)

client_id submission_date_s3 engine sap tagged_sap tagged_follow_on in_content_organic 5f4aaf58-8b0c-44a5-8208-6e64dd36e9ec 20180925 null 0 0 0 0 5f4aaf58-8b0c-44a5-8208-6e64dd36e9ec 20180925 ddg 5 0 0 0 5f4aaf58-8b0c-44a5-8208-6e64dd36e9ec 20180925 google 27 0 0 0

A client found in the table above with 0 uri and active ticks but 24 subsession hours for 1 day.   
How do they look over a week and for search?  Same pattern for 7 days and no search counts.

In [30]:
# One day's pings for client 68a8
ms_1day_test = ms_1day_raw.filter("client_id like '%f492119968a8'")
display(ms_1day_test.select(ms_1day_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date subsession_counter reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 0 0 0.0 86400 24.0 2191063 229 20180925 2018-08-31T15:00:00.0+08:00 2018-09-25T00:00:00.0+08:00 28 daily 16 2 1 null 17565 null 20180605171542 release Windows_NT 6.1 7601 2017 2018-09-25T16:00:00.176Z MozillaOnline 20180925 20180621125625 61.0 release true true null 480 Mozilla true baidu Tue, 25 Sep 2018 16:18:32 GMT 26 200 null null null null null null null CN Suzhou JS zh-CN null null null 037f0b79-b98e-41f1-a70f-14d65e694b3e d5b33e62-c7e2-4b83-b68c-00ae2947b1b2 null null null null List(default-theme@mozilla.org, false, 默认, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(rollout-release-61-tls-fallback-1-3 -> active, rollout-rdl -> active) 42 189c563e-bbbf-420a-b342-0e2850916ccc

In [31]:
ms_1week_raw_cols = ms_1week_raw.columns
ms_1week_raw_cols.remove('client_id')
# One week's pings for client 68a8
ms_1week_test = ms_1week_raw.filter("client_id like '%f492119968a8'")
display(ms_1week_test.select(ms_1week_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 0 0 0.0 86399 23.99972222222222 2018245 227 20180923 2018-08-31T15:00:00.0+08:00 2018-09-23T00:00:00.0+08:00 daily 16 2 1 null 17565 null 20180605171542 release Windows_NT 6.1 7601 2017 2018-09-23T16:00:00.187Z MozillaOnline 20180923 20180621125625 61.0 release true true null 480 Mozilla true baidu Sun, 23 Sep 2018 16:18:32 GMT 26 200 null null null null null null null CN Suzhou JS zh-CN null null null 037f0b79-b98e-41f1-a70f-14d65e694b3e 70305f80-84f3-4947-854b-fba798f8e633 null null null null List(default-theme@mozilla.org, false, 默认, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(rollout-release-61-tls-fallback-1-3 -> active, rollout-rdl -> active) 42 1523f2c3-271c-425e-9685-d94e46fce844 0 0 0.0 86418 24.005 2104663 228 20180924 2018-08-31T15:00:00.0+08:00 2018-09-24T00:00:00.0+08:00 daily 16 2 1 null 17565 null 20180605171542 release Windows_NT 6.1 7601 2017 2018-09-24T16:00:00.018Z MozillaOnline 20180924 20180621125625 61.0 release true true null 480 Mozilla true baidu Mon, 24 Sep 2018 16:18:32 GMT 26 200 null null null null null null null CN Suzhou JS zh-CN null null null 037f0b79-b98e-41f1-a70f-14d65e694b3e 155dbb97-d80c-45b6-a50b-f41d3ee6b084 null null null null List(default-theme@mozilla.org, false, 默认, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(rollout-release-61-tls-fallback-1-3 -> active, rollout-rdl -> active) 42 7991d2af-98b8-486e-92a0-4ddc0863b64f 0 0 0.0 86400 24.0 2191063 229 20180925 2018-08-31T15:00:00.0+08:00 2018-09-25T00:00:00.0+08:00 daily 16 2 1 null 17565 null 20180605171542 release Windows_NT 6.1 7601 2017 2018-09-25T16:00:00.176Z MozillaOnline 20180925 20180621125625 61.0 release true true null 480 Mozilla true baidu Tue, 25 Sep 2018 16:18:32 GMT 26 200 null null null null null null null CN Suzhou JS zh-CN null null null 037f0b79-b98e-41f1-a70f-14d65e694b3e d5b33e62-c7e2-4b83-b68c-00ae2947b1b2 null null null null List(default-theme@mozilla.org, false, 默认, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(rollout-release-61-tls-fallback-1-3 -> active, rollout-rdl -> active) 42 189c563e-bbbf-420a-b342-0e2850916ccc 0 0 0.0 86400 24.0 2277464 230 20180926 2018-08-31T15:00:00.0+08:00 2018-09-26T00:00:00.0+08:00 daily 16 2 1 null 17565 null 20180605171542 release Windows_NT 6.1 7601 2017 2018-09-26T16:00:00.228Z MozillaOnline 20180926 20180621125625 61.0 release true true null 480 Mozilla true baidu Wed, 26 Sep 2018 16:18:32 GMT 26 200 null null null null null null null CN Suzhou JS zh-CN null null null 037f0b79-b98e-41f1-a70f-14d65e694b3e 62e1890e-3416-46e7-adcc-49eddf72d736 null null null null List(default-theme@mozilla.org, false, 默认, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(rollout-release-61-tls-fallback-1-3 -> active, rollout-rdl -> active) 42 e0809e21-3698-44b8-8bcc-7624f45ddae1 0 0 0.0 86400 24.0 2363864 231 20180927 2018-08-31T15:00:00.0+08:00 2018-09-27T00:00:00.0+08:0

In [32]:
# Search counts for the week
search_week_test = search_wk.filter("client_id like '%f492119968a8'")
display(search_week_test)

client_id submission_date_s3 engine sap tagged_sap tagged_follow_on in_content_organic 014b77b1-b74f-4fe4-ade9-f492119968a8 20180925 null 0 0 0 0 014b77b1-b74f-4fe4-ade9-f492119968a8 20180924 null 0 0 0 0 014b77b1-b74f-4fe4-ade9-f492119968a8 20180927 null 0 0 0 0 014b77b1-b74f-4fe4-ade9-f492119968a8 20180926 null 0 0 0 0 014b77b1-b74f-4fe4-ade9-f492119968a8 20180928 null 0 0 0 0 014b77b1-b74f-4fe4-ade9-f492119968a8 20180923 null 0 0 0 0 014b77b1-b74f-4fe4-ade9-f492119968a8 20180929 null 0 0 0 0

#### Subsession Length is 0

In [34]:
ms_1day_ssl0 = ms_1day_raw.filter((F.col("subsession_length") == 0))
ms_1day_ssl0.count()
# Small number of pings

Out[ 128 ]: 2625

In [35]:
# Look at the details of these pings
display(ms_1day_ssl0.select(ms_1day_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date subsession_counter reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 0 0 0.0 0 0.0 754 27 20180925 2018-09-25T09:00:00.0+02:00 2018-09-25T09:00:00.0+02:00 2 shutdown 10 null null null 17691 null 20180830143136 release Windows_NT 6.1 7601 2016 2018-09-25T07:16:12.378Z null 20180925 20180920131237 62.0.2 release true true null 120 Mozilla true google Tue, 25 Sep 2018 07:16:12 GMT null null null null null null null null null DE Mainz RP en-US null null null 6872701b-70a0-4193-8e47-38038cc3cf75 51d502ee-3325-4054-87d5-0599343cbd86 null null null null List(default-theme@mozilla.org, false, Default, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null null 42 3780177e-176f-4d85-8599-8860a549f469 0 0 0.0 0 0.0 1689 7708 20180925 2018-09-25T06:00:00.0+02:00 2018-09-25T07:00:00.0+02:00 2 shutdown 10 null null null 17122 17486 null release Windows_NT 6.3 9600 2016 2018-09-25T05:05:11.150Z null 20180925 20180920131237 62.0.2 release true true null 120 Mozilla false google Tue, 25 Sep 2018 05:05:11 GMT null null null null null null null null null ES el Prat de Llobregat CT es-ES List(Windows Defender) List(Windows Defender) List(Firewall de Windows) 924d09aa-8909-476d-9cea-cba230bbcffe 3ac71f6f-5b09-426e-9d6c-6ae064c9ea9f null null null null List(default-theme@mozilla.org, false, Predeterminado, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null null 42 1dc2378b-1e65-47fb-9f9e-ecc35a0ddc16 0 0 0.0 0 0.0 2 963 20180925 2018-09-25T15:00:00.0+02:00 2018-09-25T15:00:00.0+02:00 1 shutdown 10 null null null 17124 null null release Windows_NT 10.0 17134 2018 2018-09-25T13:24:50.422Z null 20180925 20180920131237 62.0.2 release true true null 120 Mozilla null null Tue, 25 Sep 2018 13:26:14 GMT null null null null null null null false null NL Amsterdam NH nl List(AVG Antivirus) List(AVG Antivirus) List(Windows Firewall) 9714d1fe-1eaf-4ef8-a647-61e411a47d23 0b348938-f236-48f2-9c44-fe69b05bcae4 null null null null List(default-theme@mozilla.org, false, Standaard, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null null 42 947cd30b-e86c-42ad-ad65-46c42d44ea3f 0 0 0.0 0 0.0 4 3534 20180925 2018-09-25T09:00:00.0+02:00 2018-09-25T09:00:00.0+02:00 1 shutdown 8 null null null 16857 null null release Windows_NT 6.1 7601 2006 2018-09-25T07:45:31.891Z null 20180925 20180920131237 62.0.2 release true true null 120 Mozilla null null Tue, 25 Sep 2018 07:46:34 GMT null null null null null null null false null CZ Prague 10 cs null null null 4647cc22-a4b1-4c8f-a540-1ba8aad4127c 48534406-e485-48f1-ad62-1e7899f275bd null null null null List(MISSING, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null) null null 42 b1d15c5f-7b63-470f-b7db-5077d94dcee5 0 0 0.0 0 0.0 23739 602 20180925 2018-09-24T00:00:00.0+02:00 2018-09-24T00:00:00.0+02:00 2 shutdown 9 2 2 null 17177 null null release Windows_NT 10.0 17134 2018 2018-09-24T12:51:46.978Z null 20180925 20170504105526 53.0.2 release true true null 120 Mozilla false google

In [36]:
# Summary stats of pings for 1 day
display(ms_1day_ssl0['uri_count', 'active_ticks', 'active_tick_hrs', 'subsession_length', 'subsession_hours', 'session_length', 'submission_date_s3'].describe())

summary uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length submission_date_s3 count 2625 2625 2625 2625 2625 2622 2625 mean 0.011428571428571429 0.07542857142857143 1.0476190476190458E-4 0.0 0.0 119098.77040427155 2.0180925E7 stddev 0.4337413204907338 0.8706479624764873 0.001209233281217345 0.0 0.0 731224.805851591 0.0 min 0 0 0.0 0 0.0 0 20180925 max 22 43 0.059722222222222225 0 0.0 31791597 20180925

Not sure why the uri_count and active_ticks are occasionally > 0 for subsession length of 0

In [38]:
# Look at ping with subsession length 0 and active ticks > 20
ssl0 = ms_1day_ssl0.where("active_ticks > 20")
display(ssl0.select(ms_1day_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date subsession_counter reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 22 43 0.059722222222222225 0 0.0 38166 908 20180925 2018-09-24T13:00:00.0-04:00 2018-09-25T00:00:00.0-04:00 2 shutdown 11 7 1 1 17258 17575 null release Windows_NT 10.0 17134 2018 2018-09-25T04:22:33.439Z null 20180925 20180920131237 62.0.2 release true true null -240 Mozilla false google-2018 Tue, 25 Sep 2018 04:22:33 GMT null null null 1 null null null null null US Largo FL en-US List(Windows Defender Antivirus) List(Windows Defender Antivirus) List(Windows Firewall) 9c5d767d-a980-427a-9537-8dd30be6719d d774f89d-b290-4230-9db0-741bad82d2ae null null null null List(default-theme@mozilla.org, false, Default, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(searchCohort -> nov17-2) 42 c556e49e-b4e8-400b-8332-cbad1a039204

In [39]:
# Check if this ssl0 client has any search counts
search_day_test = search_day.filter("client_id like '%2e1b9e07d808'")
display(search_day_test)

client_id submission_date_s3 engine sap tagged_sap tagged_follow_on in_content_organic becb9c30-48a8-4055-bc60-2e1b9e07d808 20180925 null 0 0 0 0

Check what this ssl0 client looks like for the rest of the week  
The other pings look normal.  
profile_subsession_counter 908 is a shutdown ping with the same session_length as 907.  Perhaps these uri and active tick counts are really from the previous subsession?

In [41]:
# Check what this ssl0 client looks like for the rest of the week
ms_1week_test = ms_1week_raw.filter("client_id like '%2e1b9e07d808'")
display(ms_1week_test.select(ms_1week_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 213 1112 1.5444444444444445 43676 12.132222222222222 43720 902 20180923 2018-09-22T11:00:00.0-04:00 2018-09-22T11:00:00.0-04:00 daily 11 10 2 6 17258 17575 null release Windows_NT 10.0 17134 2018 2018-09-23T04:02:56.859Z null 20180923 20180830143136 62.0 release true true null -240 Mozilla false google-2018 Sun, 23 Sep 2018 04:22:13 GMT 140 20768 null 24 2 null null true null US Largo FL en-US List(Windows Defender Antivirus) List(Windows Defender Antivirus) List(Windows Firewall) e45778d4-10b6-4a30-a5c4-bcd37abd55dc dded3083-26ac-4c0a-b829-ab7a8b151fab null null null null List(default-theme@mozilla.org, false, Default, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(searchCohort -> nov17-2) 42 3ab8347a-24b5-4dac-91b6-a2dae2d539dd 49 290 0.4027777777777778 13249 3.680277777777778 56970 903 20180923 2018-09-22T11:00:00.0-04:00 2018-09-23T00:00:00.0-04:00 shutdown 11 9 1 2 17258 17575 null release Windows_NT 10.0 17134 2018 2018-09-23T07:43:46.609Z null 20180923 20180830143136 62.0 release true true null -240 Mozilla false google-2018 Sun, 23 Sep 2018 07:43:46 GMT null null null 1 null null null null null US Largo FL en-US List(Windows Defender Antivirus) List(Windows Defender Antivirus) List(Windows Firewall) e45778d4-10b6-4a30-a5c4-bcd37abd55dc 33af7969-1012-490a-a694-54881e58a27c null null null null List(default-theme@mozilla.org, false, Default, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(searchCohort -> nov17-2) 42 f03fc52c-9c38-4ef1-a807-926eac9eb24e 162 936 1.3 42447 11.790833333333333 42450 904 20180924 2018-09-23T12:00:00.0-04:00 2018-09-23T12:00:00.0-04:00 daily 9 7 1 3 17258 17575 20180830143136 release Windows_NT 10.0 17134 2018 2018-09-24T04:04:44.314Z null 20180924 20180920131237 62.0.2 release true true null -240 Mozilla false google-2018 Mon, 24 Sep 2018 04:21:18 GMT 141 20856 null 11 null null null true null US Largo FL en-US List(Windows Defender Antivirus) List(Windows Defender Antivirus) List(Windows Firewall) e2621585-ec4d-4814-9b37-1d964fa1259a 8953643f-ca39-4d03-a226-af5a1fa9cfd8 null null null null List(default-theme@mozilla.org, false, Default, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(searchCohort -> nov17-2) 42 b1576189-c3d0-44f0-9ef9-2c1eecf322eb 6 35 0.04861111111111111 2139 0.5941666666666666 44589 905 20180924 2018-09-23T12:00:00.0-04:00 2018-09-24T00:00:00.0-04:00 environment-change 9 8 1 1 17258 17575 20180830143136 release Windows_NT 10.0 17134 2018 2018-09-24T04:40:23.369Z null 20180924 20180920131237 62.0.2 release true true null -240 Mozilla false google-2018 Mon, 24 Sep 2018 04:40:23 GMT null null null 1 null null null null null US Largo FL en-US List(Windows Defender Antivirus) List(Windows Defender Antivirus) List(Windows Firewall) e2621585-ec4d-4814-9b37-1d964fa1259a 3f880244-709e-42fc-b8ea-422c95baf80b null null null null List(default-theme@mozilla.org, false, Default, false, false, , 1, nu

#### High Active Ticks

In [43]:
# Summary stats for pings with active ticks greater than 1440
ms_1day_high_at = ms_1day_raw.filter(F.col("active_ticks") > 1440)
ms_1day_high_at['uri_count', 'active_ticks', 'active_tick_hrs', 'subsession_length', 'subsession_hours'].describe().show()

+-------+-----------------+------------------+------------------+-----------------+------------------+
summary| uri_count| active_ticks| active_tick_hrs|subsession_length| subsession_hours|
+-------+-----------------+------------------+------------------+-----------------+------------------+
 count| 43020| 43020| 43020| 43020| 43020|
 mean|475.5163179916318|2140.9614132961415|2.9735575184668623|40986.65990237099|11.385183306214161|
 stddev|746.2481411619434| 814.1989465666271|1.1308318702314273|75664.86104367331|21.018016956575917|
 min| 0| 1441| 2.001388888888889| 7260|2.0166666666666666|
 max| 59950| 17273|23.990277777777777| 12840921| 3566.9225|
+-------+-----------------+------------------+------------------+-----------------+------------------+

Let's look at one client's use over a week for the highest active_ticks value.  
Is this a bot?  0 uri, active 24 hours 7 days a week, in Moscow.

In [45]:
# Look at client bcc2 over 1 week of pings
highat_c = ms_1week_raw.where("client_id like '%f1407e1fbcc2'").sort("submission_date_s3")
display(highat_c.select(ms_1week_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 0 12346 17.147222222222222 61956 17.21 15041813 609 20180923 2018-04-02T14:00:00.0+03:00 2018-09-23T00:00:00.0+03:00 environment-change 11 1 1 null 16193 null 20170926190823 release Windows_NT 6.1 7601 2014 2018-09-23T14:12:36.570Z null 20180923 20180315233128 59.0.1 release true true null 180 Mozilla true yandex-ru Sun, 23 Sep 2018 14:12:36 GMT 13 277 null null null null null null null RU Moscow MOW ru null null null a1430ead-6812-406c-ad20-8306ac0a1e4f 1b4ec69f-bfb8-4aa7-ab5d-2f5868d75d0c null null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Стандартная, false, false, 59.0.1, 4, null, false, false, 16193, 17623, null, null, null, null) null null 42 326b00c1-e42e-428b-ae2d-df1eddbe64fb 0 4886 6.786111111111111 24443 6.789722222222222 15066256 610 20180923 2018-04-02T14:00:00.0+03:00 2018-09-23T17:00:00.0+03:00 daily 11 1 1 null 16193 null 20170926190823 release Windows_NT 6.1 7601 2014 2018-09-23T21:00:00.008Z null 20180923 20180315233128 59.0.1 release true true null 180 Mozilla true yandex-ru Sun, 23 Sep 2018 21:16:01 GMT null null null null null null null null null RU Moscow MOW ru null null null a1430ead-6812-406c-ad20-8306ac0a1e4f 6f458b8b-9968-472f-95a4-a9dfab1cd756 null null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Стандартная, false, false, 59.0.1, 4, null, false, false, 16193, 17623, null, null, null, null) null null 42 ada1b581-877a-4e80-8eb9-7d6fe9c5352d 0 17272 23.988888888888887 86395 23.99861111111111 15152652 611 20180924 2018-04-02T14:00:00.0+03:00 2018-09-24T00:00:00.0+03:00 daily 11 1 1 null 16193 null 20170926190823 release Windows_NT 6.1 7601 2014 2018-09-24T21:00:00.016Z null 20180924 20180315233128 59.0.1 release true true null 180 Mozilla true yandex-ru Mon, 24 Sep 2018 21:16:01 GMT 13 277 null null null null null null null RU Moscow MOW ru null null null a1430ead-6812-406c-ad20-8306ac0a1e4f 2f9f8a46-8125-4471-ac08-f31f2db62ca7 null null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Стандартная, false, false, 59.0.1, 4, null, false, false, 16193, 17623, null, null, null, null) null null 42 881259a1-2f16-459c-beb0-42c37faf8211 0 17273 23.990277777777777 86400 24.0 15239052 612 20180925 2018-04-02T14:00:00.0+03:00 2018-09-25T00:00:00.0+03:00 daily 11 1 1 null 16193 null 20170926190823 release Windows_NT 6.1 7601 2014 2018-09-25T21:00:00.008Z null 20180925 20180315233128 59.0.1 release true true null 180 Mozilla true yandex-ru Tue, 25 Sep 2018 21:16:01 GMT 13 277 null null null null null null null RU Moscow MOW ru null null null a1430ead-6812-406c-ad20-8306ac0a1e4f cf220b52-7b66-4506-a177-66119183a8ef null null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Стандартная, false, false, 59.0.1, 4, null, false, false, 16193, 17623, null, null, null, null) null null 42 998cf097-6e44-4ea1-b6af-0f19ea5b5113 0 17272 23.988888888888887 86399 23.99972222222222 15325452 613 20180926 2018-04-02T14:00:00.0+03:00 2018-09-26T00:00:00.0+03:00 daily 11 1 

The usage is 24 hours every day.  These numbers look a bit different than that because there is 1 day with 2 subsessions.

In [47]:
# Summary stats for client bcc2 over a week
highat_c['uri_count', 'active_ticks', 'active_tick_hrs', 'subsession_length', 'subsession_hours'].describe().show()

+-------+---------+-----------------+------------------+-----------------+-----------------+
summary|uri_count| active_ticks| active_tick_hrs|subsession_length| subsession_hours|
+-------+---------+-----------------+------------------+-----------------+-----------------+
 count| 8| 8| 8| 8| 8|
 mean| 0.0| 15108.375|20.983854166666664| 75598.875| 20.9996875|
 stddev| 0.0|4475.780696066968| 6.216362077870788|22369.82854163489|6.213841261565247|
 min| 0| 4886| 6.786111111111111| 24443|6.789722222222222|
 max| 0| 17273|23.990277777777777| 86400| 24.0|
+-------+---------+-----------------+------------------+-----------------+-----------------+

Does this pattern hold up over more than 1 week?  
Yes over 4 weeks

In [49]:
# Look at client bcc2 over 4 weeks of pings
highat_c4w = ms_4week_raw.where("client_id like '%f1407e1fbcc2'").sort("profile_subsession_counter", "submission_date_s3")
display(highat_c4w.select(ms_1week_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 0 12346 17.147222222222222 61956 17.21 15041813 609 20180923 2018-04-02T14:00:00.0+03:00 2018-09-23T00:00:00.0+03:00 environment-change 11 1 1 null 16193 null 20170926190823 release Windows_NT 6.1 7601 2014 2018-09-23T14:12:36.570Z null 20180923 20180315233128 59.0.1 release true true null 180 Mozilla true yandex-ru Sun, 23 Sep 2018 14:12:36 GMT 13 277 null null null null null null null RU Moscow MOW ru null null null a1430ead-6812-406c-ad20-8306ac0a1e4f 1b4ec69f-bfb8-4aa7-ab5d-2f5868d75d0c null null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Стандартная, false, false, 59.0.1, 4, null, false, false, 16193, 17623, null, null, null, null) null null 42 326b00c1-e42e-428b-ae2d-df1eddbe64fb 0 4886 6.786111111111111 24443 6.789722222222222 15066256 610 20180923 2018-04-02T14:00:00.0+03:00 2018-09-23T17:00:00.0+03:00 daily 11 1 1 null 16193 null 20170926190823 release Windows_NT 6.1 7601 2014 2018-09-23T21:00:00.008Z null 20180923 20180315233128 59.0.1 release true true null 180 Mozilla true yandex-ru Sun, 23 Sep 2018 21:16:01 GMT null null null null null null null null null RU Moscow MOW ru null null null a1430ead-6812-406c-ad20-8306ac0a1e4f 6f458b8b-9968-472f-95a4-a9dfab1cd756 null null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Стандартная, false, false, 59.0.1, 4, null, false, false, 16193, 17623, null, null, null, null) null null 42 ada1b581-877a-4e80-8eb9-7d6fe9c5352d 0 17272 23.988888888888887 86395 23.99861111111111 15152652 611 20180924 2018-04-02T14:00:00.0+03:00 2018-09-24T00:00:00.0+03:00 daily 11 1 1 null 16193 null 20170926190823 release Windows_NT 6.1 7601 2014 2018-09-24T21:00:00.016Z null 20180924 20180315233128 59.0.1 release true true null 180 Mozilla true yandex-ru Mon, 24 Sep 2018 21:16:01 GMT 13 277 null null null null null null null RU Moscow MOW ru null null null a1430ead-6812-406c-ad20-8306ac0a1e4f 2f9f8a46-8125-4471-ac08-f31f2db62ca7 null null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Стандартная, false, false, 59.0.1, 4, null, false, false, 16193, 17623, null, null, null, null) null null 42 881259a1-2f16-459c-beb0-42c37faf8211 0 17273 23.990277777777777 86400 24.0 15239052 612 20180925 2018-04-02T14:00:00.0+03:00 2018-09-25T00:00:00.0+03:00 daily 11 1 1 null 16193 null 20170926190823 release Windows_NT 6.1 7601 2014 2018-09-25T21:00:00.008Z null 20180925 20180315233128 59.0.1 release true true null 180 Mozilla true yandex-ru Tue, 25 Sep 2018 21:16:01 GMT 13 277 null null null null null null null RU Moscow MOW ru null null null a1430ead-6812-406c-ad20-8306ac0a1e4f cf220b52-7b66-4506-a177-66119183a8ef null null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Стандартная, false, false, 59.0.1, 4, null, false, false, 16193, 17623, null, null, null, null) null null 42 998cf097-6e44-4ea1-b6af-0f19ea5b5113 0 17272 23.988888888888887 86399 23.99972222222222 15325452 613 20180926 2018-04-02T14:00:00.0+03:00 2018-09-26T00:00:00.0+03:00 daily 11 1 

In [50]:
# Summary stats for 4 weeks for client bcc2
highat_c4w['uri_count', 'active_ticks', 'active_tick_hrs', 'subsession_length', 'subsession_hours'].describe().show()

+-------+---------+-----------------+------------------+-----------------+-----------------+
summary|uri_count| active_ticks| active_tick_hrs|subsession_length| subsession_hours|
+-------+---------+-----------------+------------------+-----------------+-----------------+
 count| 32| 32| 32| 32| 32|
 mean| 0.0| 15112.28125|20.989279513888903| 75598.78125|20.99966145833333|
 stddev| 0.0|4251.971316887862| 5.905515717899807|21264.27532913326| 5.90674314698146|
 min| 0| 4877| 6.773611111111111| 24393|6.775833333333333|
 max| 0| 17274|23.991666666666667| 86400| 24.0|
+-------+---------+-----------------+------------------+-----------------+-----------------+

0 uri, active 24 hours not every day for 12 weeks but the majority of them

In [52]:
ms_12week_raw_cols = ms_12week_raw.columns
ms_12week_raw_cols.remove('client_id')
# Look at client bcc2 over 12 weeks of pings
highat_c12w = ms_12week_raw.where("client_id like '%f1407e1fbcc2'").sort("profile_subsession_counter", "submission_date_s3")
display(highat_c12w.select(ms_12week_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason 0 12346 17.147222222222222 61956 17.21 15041813 609 20180923 2018-04-02T14:00:00.0+03:00 2018-09-23T00:00:00.0+03:00 environment-change 0 4886 6.786111111111111 24443 6.789722222222222 15066256 610 20180923 2018-04-02T14:00:00.0+03:00 2018-09-23T17:00:00.0+03:00 daily 0 17272 23.988888888888887 86395 23.99861111111111 15152652 611 20180924 2018-04-02T14:00:00.0+03:00 2018-09-24T00:00:00.0+03:00 daily 0 17273 23.990277777777777 86400 24.0 15239052 612 20180925 2018-04-02T14:00:00.0+03:00 2018-09-25T00:00:00.0+03:00 daily 0 17272 23.988888888888887 86399 23.99972222222222 15325452 613 20180926 2018-04-02T14:00:00.0+03:00 2018-09-26T00:00:00.0+03:00 daily 0 17273 23.990277777777777 86399 23.99972222222222 15411852 614 20180927 2018-04-02T14:00:00.0+03:00 2018-09-27T00:00:00.0+03:00 daily 0 17273 23.990277777777777 86400 24.0 15498252 615 20180928 2018-04-02T14:00:00.0+03:00 2018-09-28T00:00:00.0+03:00 daily 0 17272 23.988888888888887 86399 23.99972222222222 15584652 616 20180929 2018-04-02T14:00:00.0+03:00 2018-09-29T00:00:00.0+03:00 daily 0 17274 23.991666666666667 86399 23.99972222222222 15671052 617 20180930 2018-04-02T14:00:00.0+03:00 2018-09-30T00:00:00.0+03:00 daily 0 17271 23.9875 86395 23.99861111111111 15757447 618 20181001 2018-04-02T14:00:00.0+03:00 2018-10-01T00:00:00.0+03:00 daily 0 17273 23.990277777777777 86399 23.99972222222222 15843847 619 20181002 2018-04-02T14:00:00.0+03:00 2018-10-02T00:00:00.0+03:00 daily 0 12397 17.218055555555555 62006 17.22388888888889 15905854 620 20181003 2018-04-02T14:00:00.0+03:00 2018-10-03T00:00:00.0+03:00 environment-change 0 4877 6.773611111111111 24393 6.775833333333333 15930247 621 20181003 2018-04-02T14:00:00.0+03:00 2018-10-03T17:00:00.0+03:00 daily 0 17272 23.988888888888887 86400 24.0 16016647 622 20181005 2018-04-02T14:00:00.0+03:00 2018-10-04T00:00:00.0+03:00 daily 0 12388 17.205555555555556 61964 17.212222222222223 16078612 623 20181005 2018-04-02T14:00:00.0+03:00 2018-10-05T00:00:00.0+03:00 environment-change 0 4884 6.783333333333333 24435 6.7875 16103047 624 20181005 2018-04-02T14:00:00.0+03:00 2018-10-05T17:00:00.0+03:00 daily 0 17273 23.990277777777777 86399 23.99972222222222 16189447 625 20181006 2018-04-02T14:00:00.0+03:00 2018-10-06T00:00:00.0+03:00 daily 0 17273 23.990277777777777 86400 24.0 16275847 626 20181007 2018-04-02T14:00:00.0+03:00 2018-10-07T00:00:00.0+03:00 daily 0 17272 23.988888888888887 86395 23.99861111111111 16362243 627 20181008 2018-04-02T14:00:00.0+03:00 2018-10-08T00:00:00.0+03:00 daily 0 17273 23.990277777777777 86399 23.99972222222222 16448643 628 20181009 2018-04-02T14:00:00.0+03:00 2018-10-09T00:00:00.0+03:00 daily 0 17273 23.990277777777777 86400 24.0 16535043 629 20181010 2018-04-02T14:00:00.0+03:00 2018-10-10T00:00:00.0+03:00 daily 0 17273 23.990277777777777 86399 23.99972222222222 16621443 630 20181011 2018-04-02T14:00:00.0+03:00 2018-10-11T00:00:00.0+03:00 daily 0 17273 23.990277777777777 86399 23.99972222222222 16707843 631 20181012 2018-04-02T14:00:00.0+03:00 2018-10-12T00:00:00.0+03:00 daily 0 17273 23.990277777777777 86399 23.99972222222222 16794243 632 20181013 2018-04-02T14:00:00.0+03:00 2018-10-13T00:00:00.0+03:00 daily 0 17272 23.988888888888887 86399 23.99972222222222 16880643 633 20181014 2018-04-02T14:00:00.0+03:00 2018-10-14T00:00:00.0+03:00 daily 0 17272 23.988888888888887 86395 23.99861111111111 16967039 634 20181015 2018-04-02T14:00:00.0+03:00 2018-10-15T00:00:00.0+03:00 daily 0 17272 23.988888888888887 86399 23.99972222222222 17053439 635 20181016 2018-04-02T14:00:00.0+03:00 2018-10-16T00:00:00.0+03:00 daily 0 17273 23.990277777777777 86399 23.99972222222222 17139839 636 20181017 2018-04-02T14:00:00.0+03:00 2018-10-17T00:00:00.0+03:00 daily 0 12390 17.208333333333332 61976 17.215555555555557 17201815 637 20181018 2018-04-02T14:00:00.0+03:00 

In [53]:
# Look at pings over 12 weeks where uri count is not 0
display(highat_c12w.where("uri_count > 0"))

client_id uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason ec05d93d-c4a8-4b07-8930-f1407e1fbcc2 1 17204 23.894444444444446 86469 24.019166666666667 17917503 646 20181026 2018-04-02T14:00:00.0+03:00 2018-10-26T00:00:00.0+03:00 daily ec05d93d-c4a8-4b07-8930-f1407e1fbcc2 6 17066 23.70277777777778 86316 23.976666666666667 18263030 650 20181030 2018-04-02T14:00:00.0+03:00 2018-10-30T00:00:00.0+03:00 daily ec05d93d-c4a8-4b07-8930-f1407e1fbcc2 5 6250 8.680555555555555 86403 24.000833333333333 642211 660 20181107 2018-10-31T13:00:00.0+03:00 2018-11-07T00:00:00.0+03:00 daily ec05d93d-c4a8-4b07-8930-f1407e1fbcc2 41 17108 23.761111111111113 86403 24.000833333333333 728614 661 20181108 2018-10-31T13:00:00.0+03:00 2018-11-08T00:00:00.0+03:00 daily ec05d93d-c4a8-4b07-8930-f1407e1fbcc2 1 41 0.05694444444444444 146534 40.70388888888889 1134131 665 20181113 2018-10-31T13:00:00.0+03:00 2018-11-12T00:00:00.0+03:00 daily ec05d93d-c4a8-4b07-8930-f1407e1fbcc2 11 13331 18.51527777777778 66747 18.54083333333333 2955127 688 20181204 2018-10-31T13:00:00.0+03:00 2018-12-04T00:00:00.0+03:00 shutdown ec05d93d-c4a8-4b07-8930-f1407e1fbcc2 2 2597 3.6069444444444443 15383 4.273055555555556 15388 689 20181204 2018-12-04T18:00:00.0+03:00 2018-12-04T18:00:00.0+03:00 environment-change ec05d93d-c4a8-4b07-8930-f1407e1fbcc2 4 11700 16.25 60716 16.865555555555556 253408 695 20181207 2018-12-04T18:00:00.0+03:00 2018-12-07T00:00:00.0+03:00 shutdown ec05d93d-c4a8-4b07-8930-f1407e1fbcc2 3 4844 6.727777777777778 24600 6.833333333333333 25157 697 20181207 2018-12-07T17:00:00.0+03:00 2018-12-07T17:00:00.0+03:00 daily ec05d93d-c4a8-4b07-8930-f1407e1fbcc2 6 17017 23.634722222222223 86403 24.000833333333333 284367 700 20181210 2018-12-07T17:00:00.0+03:00 2018-12-10T00:00:00.0+03:00 daily

In [54]:
# Summary stats for 12 weeks for 1 client id
highat_c12w['uri_count', 'active_ticks', 'active_tick_hrs', 'subsession_length', 'subsession_hours'].describe().show()

+-------+------------------+------------------+------------------+------------------+-------------------+
summary| uri_count| active_ticks| active_tick_hrs| subsession_length| subsession_hours|
+-------+------------------+------------------+------------------+------------------+-------------------+
 count| 97| 97| 97| 97| 97|
 mean|0.8247422680412371| 12424.62886597938|17.256428980526913| 74816.58762886598| 20.782385452462776|
 stddev| 4.406459059528293|6928.9030206200805| 9.62347641752789|25560.564105893904| 7.100156696081641|
 min| 0| 0| 0.0| 553|0.15361111111111111|
 max| 41| 17274|23.991666666666667| 146534| 40.70388888888889|
+-------+------------------+------------------+------------------+------------------+-------------------+

#####How many other clients have high active ticks and 0 uri in 1 week?

In [56]:
# Look at all clients over a week of pings where uri count is 0 and active ticks hours > 23
highat_w = ms_1week_raw.filter((F.col("uri_count") == 0) & (F.col("active_tick_hrs") > 23))
display(highat_w.select(ms_1week_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 0 17272 23.988888888888887 86403 24.000833333333333 833870 101 20180923 2018-09-14T08:00:00.0+03:00 2018-09-23T00:00:00.0+03:00 daily 10 1 1 null 15821 null null release Windows_NT 6.2 9200 2013 2018-09-23T21:04:34.228Z null 20180923 20180807170231 61.0.2 release true true null 180 Mozilla false yandex-ru Sun, 23 Sep 2018 21:35:16 GMT null null null null null null null null null RU Moscow MOW ru null null null 2094c4fe-989e-4565-9f40-2797a8f7bf06 a9b2c83f-185d-4231-8e18-cf9746c35e72 null null null null List(default-theme@mozilla.org, false, По умолчанию, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(rollout-release-61-tls-fallback-1-3 -> active, rollout-restart-manager-release-1481278 -> active) 42 ca25de41-8fa0-46df-9da2-0b8c8e47039b 0 17272 23.988888888888887 86403 24.000833333333333 920274 102 20180924 2018-09-14T08:00:00.0+03:00 2018-09-24T00:00:00.0+03:00 daily 10 1 1 null 15821 null null release Windows_NT 6.2 9200 2013 2018-09-24T21:04:37.740Z null 20180924 20180807170231 61.0.2 release true true null 180 Mozilla false yandex-ru Mon, 24 Sep 2018 21:35:16 GMT null null null null null null null null null RU Moscow MOW ru null null null 2094c4fe-989e-4565-9f40-2797a8f7bf06 27ed1229-4a0d-4355-92f9-1dd1e0cb73ed null null null null List(default-theme@mozilla.org, false, По умолчанию, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(rollout-release-61-tls-fallback-1-3 -> active, rollout-restart-manager-release-1481278 -> active) 42 c92ce714-d9fe-44b6-83c5-3b93b2ac9fa4 0 17280 24.0 86401 24.00027777777778 799713 14 20180923 2018-09-13T17:00:00.0+00:00 2018-09-22T00:00:00.0+00:00 daily 11 4 1 null 17787 null null release Linux 4.14.10 null null 2018-09-23T00:02:15.395Z null 20180923 20180830143136 62.0 release true true null 0 Mozilla false google-2018 Sun, 23 Sep 2018 00:59:04 GMT null null null null null null null null null US Los Angeles CA en-US null null null acf4222b-3a74-4443-a209-6e5776a862a8 de01eb76-1ea2-4dec-86bb-fc900a06dd4c null null null null List(default-theme@mozilla.org, false, Default, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(searchCohort -> nov17-2, prefflip-activity-stream-simplified-onboarding-overlay-v1-0-1473580 -> variant2, searchNudgesExperiment -> doshow) 42 8060b37b-9a01-4aff-acb0-51fff41ced63 0 17279 23.99861111111111 86401 24.00027777777778 886115 15 20180924 2018-09-13T17:00:00.0+00:00 2018-09-23T00:00:00.0+00:00 daily 11 4 1 null 17787 null null release Linux 4.14.10 null null 2018-09-24T00:02:17.357Z null 20180924 20180830143136 62.0 release true true null 0 Mozilla false google-2018 Mon, 24 Sep 2018 00:59:04 GMT null null null null null null null null null US Los Angeles CA en-US null null null acf4222b-3a74-4443-a209-6e5776a862a8 df2067a6-c36b-4d2c-8fdc-ab7cd26f3af7 null null null null List(default-theme@mozilla.org, false, Default, false, false, , 1, null, false, false, 0, 0, null, null, null, null)

18 distinct clients

In [58]:
# Count distinct clients over a week where uri count is 0 and active ticks hours > 23
highat_clients = highat_w.select("client_id").distinct()
highat_clients.count()

Out[ 143 ]: 18

In [59]:
# Look at client ids where uri count is 0 and active ticks hours > 23
display(highat_clients)

client_id 6693ef5a-7ae3-424e-b59c-2995a7d66a8e 5320032f-bf72-4e4e-a8c3-fdf98a07395e 4f2249de-cbbb-4132-9293-7392caf20c95 4096a69e-10b7-4b48-b03b-9f1e1736ea86 e4dd44e7-169c-48fa-969e-d8efa8322154 cb8b8762-1515-4892-a6c9-6b79a09f2673 61d864f6-423d-4a97-8f10-c86d7f20cdec 045374f7-7698-447c-9ad6-4ae67e57531b 78e051ab-cfda-47db-a949-5477e70c6128 73ec4002-261b-4bb2-a17c-88bd6ddb6e37 4c522c98-9aff-4ba0-9040-536100560f8f d972a068-2feb-494a-a585-7e5d7ee9164a 4d568b0d-fc9d-4c29-a688-7ba89fbb29ad eb70fac3-1f11-4fe2-b24c-fe5b8e541450 2bd0eb44-ee67-4819-8252-ce7ee166ecca e2e76a8a-5c3c-4978-bd73-94681e62715e 1de50f9f-9ae8-4c41-bcf2-bf586721411b ec05d93d-c4a8-4b07-8930-f1407e1fbcc2

Look at some of the additional clients

This client looks like "normal"/mixed usage.  
Only one day of 0 uri and 24 hrs active, profile_subsession_counter in order, some short subsessions, some high active ticks with non-zero uris.

In [62]:
# Look at 1 week of pings for client 6a8e
highat_c1 = ms_1week_raw.where("client_id like '%2995a7d66a8e'").sort("submission_date_s3")
display(highat_c1.select(ms_1week_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 0 17262 23.975 86404 24.00111111111111 228667 1994 20180923 2018-09-21T08:00:00.0+02:00 2018-09-23T00:00:00.0+02:00 daily 12 5 2 null 16607 null null release Windows_NT 6.1 7601 2012 2018-09-23T22:01:44.806Z null 20180923 20180830143136 62.0 release true true null 120 Mozilla true other-Bing Search Engine Sun, 23 Sep 2018 22:09:11 GMT null null null null null null null null null DE Lübeck SH de null null null 9dec62b9-ed9e-4981-b7d2-6f7ce0e5646b 31b7ba31-e1bf-4452-9790-0b986b62cefd null null null null List(MISSING, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null) null Map(prefflip-gls-key-1490454 -> variant) 42 7445b4e9-d4b7-4ec9-82f8-45f482f4ef5e 244 3248 4.511111111111111 26325 7.3125 288554 1996 20180924 2018-09-21T08:00:00.0+02:00 2018-09-24T09:00:00.0+02:00 environment-change 12 11 2 8 16607 null null release Windows_NT 6.1 7601 2012 2018-09-24T14:39:51.327Z null 20180924 20180830143136 62.0 release true true null 120 Mozilla true other-Bing Search Engine Mon, 24 Sep 2018 14:39:51 GMT null null null 5 null null null null null DE Lübeck SH de null null null 9dec62b9-ed9e-4981-b7d2-6f7ce0e5646b 499f46a0-ff03-488d-892a-e314dec8ebfd null null null null List(MISSING, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null) null Map(prefflip-gls-key-1490454 -> variant) 42 eaf4f3fd-8a65-47b9-972b-ccfde62cf727 0 518 0.7194444444444444 26701 7.416944444444445 315255 1997 20180924 2018-09-21T08:00:00.0+02:00 2018-09-24T16:00:00.0+02:00 daily 12 9 2 null 16607 null null release Windows_NT 6.1 7601 2012 2018-09-24T22:04:52.993Z null 20180924 20180830143136 62.0 release true true null 120 Mozilla true other-Bing Search Engine Mon, 24 Sep 2018 22:09:11 GMT null null null null null null null null null DE Lübeck SH de null null null 9dec62b9-ed9e-4981-b7d2-6f7ce0e5646b 0c3eaef4-2b08-450c-8381-4f2b3fec97be null null null null List(MISSING, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null) null Map(prefflip-gls-key-1490454 -> variant) 42 9b5933ad-1e64-4470-a048-d51f0a93e4c2 112 6162 8.558333333333334 33560 9.322222222222223 262228 1995 20180924 2018-09-21T08:00:00.0+02:00 2018-09-24T00:00:00.0+02:00 environment-change 12 8 2 8 16607 null null release Windows_NT 6.1 7601 2012 2018-09-24T07:21:05.457Z null 20180924 20180830143136 62.0 release true true null 120 Mozilla true other-Bing Search Engine Mon, 24 Sep 2018 07:21:05 GMT 81 35792 null 5 null null null null null DE Lübeck SH de null null null 9dec62b9-ed9e-4981-b7d2-6f7ce0e5646b 92f44168-a354-480c-b4ae-37e1855b2160 null null null null List(MISSING, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null) null Map(prefflip-gls-key-1490454 -> variant) 42 ab616bfd-401c-443f-943b-fd12564f84aa 32 126 0.175 1110 0.30833333333333335 349977 2000 20180925 2018-09-21T08:00:00.0+02:00 2018-09-25T09:00:00.0+02:00 environment-change 12 12 3 1 16607 null n

Low search counts, but not 0

In [64]:
# Look at search counts for client 6a8e
search_wk_test = search_wk.filter("client_id like '%2995a7d66a8e'")
display(search_wk_test)

client_id submission_date_s3 engine sap tagged_sap tagged_follow_on in_content_organic 6693ef5a-7ae3-424e-b59c-2995a7d66a8e 20180924 null 0 0 0 0 6693ef5a-7ae3-424e-b59c-2995a7d66a8e 20180926 google 0 0 0 1 6693ef5a-7ae3-424e-b59c-2995a7d66a8e 20180928 other-Bing Search Engine 5 0 0 0 6693ef5a-7ae3-424e-b59c-2995a7d66a8e 20180926 null 0 0 0 0 6693ef5a-7ae3-424e-b59c-2995a7d66a8e 20180927 null 0 0 0 0 6693ef5a-7ae3-424e-b59c-2995a7d66a8e 20180923 null 0 0 0 0 6693ef5a-7ae3-424e-b59c-2995a7d66a8e 20180929 null 0 0 0 0 6693ef5a-7ae3-424e-b59c-2995a7d66a8e 20180925 other-Bing Search Engine 1 0 0 0 6693ef5a-7ae3-424e-b59c-2995a7d66a8e 20180928 null 0 0 0 0 6693ef5a-7ae3-424e-b59c-2995a7d66a8e 20180926 other-Bing Search Engine 2 0 0 0 6693ef5a-7ae3-424e-b59c-2995a7d66a8e 20180925 google 0 0 0 7 6693ef5a-7ae3-424e-b59c-2995a7d66a8e 20180925 null 0 0 0 0 6693ef5a-7ae3-424e-b59c-2995a7d66a8e 20180928 google 0 0 0 5

This second client also has "normal" usage - 7 daily pings, profile_subsession_counter in order, short active tick hours and only 1 odd record with 0 uri and 24 active tick hours

In [66]:
# Look at 1 week of pings for client 395e
highat_c2 = ms_1week_raw.where("client_id like '%fdf98a07395e'").sort("submission_date_s3")
display(highat_c2.select(ms_1week_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 0 0 0.0 86397 23.999166666666667 315893 1326 20180923 2018-09-20T08:00:00.0+03:00 2018-09-23T00:00:00.0+03:00 daily 10 1 1 null 15964 null null release Windows_NT 10.0 17134 2018 2018-09-23T21:00:00.019Z null 20180923 20180830143136 62.0 release true true null 180 Mozilla false google Sun, 23 Sep 2018 21:49:29 GMT 16 47987 null null null null null null null FI ?? null fi List(Windows Defenderin virustentorjunta) List(Windows Defenderin virustentorjunta) List(Windowsin palomuuri) 02e8353c-f693-46dc-b4fa-47580d764c84 fd5213a1-02dd-4af2-b7c5-1879543cc489 null null null null List(default-theme@mozilla.org, false, Oletus, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null null 42 2281924f-8d5a-4ace-a9d0-f6307f2ea237 0 0 0.0 86397 23.999166666666667 402290 1327 20180924 2018-09-20T08:00:00.0+03:00 2018-09-24T00:00:00.0+03:00 daily 10 1 1 null 15964 null null release Windows_NT 10.0 17134 2018 2018-09-24T21:00:00.025Z null 20180924 20180830143136 62.0 release true true null 180 Mozilla false google Mon, 24 Sep 2018 21:49:29 GMT 16 47987 null null null null null null null FI ?? null fi List(Windows Defenderin virustentorjunta) List(Windows Defenderin virustentorjunta) List(Windowsin palomuuri) 02e8353c-f693-46dc-b4fa-47580d764c84 0352e6aa-2568-4bb6-9fb6-cf2341fcb190 null null null null List(default-theme@mozilla.org, false, Oletus, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null null 42 18596f43-19e7-4aab-946e-42d29948833e 60 3204 4.45 86663 24.073055555555555 488953 1328 20180925 2018-09-20T08:00:00.0+03:00 2018-09-25T00:00:00.0+03:00 daily 10 3 2 4 15964 null null release Windows_NT 10.0 17134 2018 2018-09-25T21:04:23.651Z null 20180925 20180830143136 62.0 release true true null 180 Mozilla false google Tue, 25 Sep 2018 21:49:29 GMT 16 47987 null 2 1 null null null null FI ?? null fi List(Windows Defenderin virustentorjunta) List(Windows Defenderin virustentorjunta) List(Windowsin palomuuri) 02e8353c-f693-46dc-b4fa-47580d764c84 0a529373-0f49-440e-bf54-6c08be651f64 null null null null List(default-theme@mozilla.org, false, Oletus, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null null 42 68e9f1ca-3781-48d7-9913-0170631337f3 0 17252 23.961111111111112 86404 24.00111111111111 575358 1329 20180926 2018-09-20T08:00:00.0+03:00 2018-09-26T00:00:00.0+03:00 daily 10 2 2 null 15964 null null release Windows_NT 10.0 17134 2018 2018-09-26T21:04:28.368Z null 20180926 20180830143136 62.0 release true true null 180 Mozilla false google Wed, 26 Sep 2018 21:49:29 GMT null null null null null null null null null FI ?? null fi List(Windows Defenderin virustentorjunta) List(Windows Defenderin virustentorjunta) List(Windowsin palomuuri) 02e8353c-f693-46dc-b4fa-47580d764c84 1ac3806d-3d39-4ba7-9ad4-57d12f8a4512 null null null null List(default-theme@mozilla.org, false, Oletus, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null null 42 c4e25669-de0d-4a57-912b-f04

In [67]:
# Look at search counts for client 395e
search_wk_test = search_wk.filter("client_id like '%fdf98a07395e'")
display(search_wk_test)

client_id submission_date_s3 engine sap tagged_sap tagged_follow_on in_content_organic 5320032f-bf72-4e4e-a8c3-fdf98a07395e 20180926 null 0 0 0 0 5320032f-bf72-4e4e-a8c3-fdf98a07395e 20180929 google 2 2 0 0 5320032f-bf72-4e4e-a8c3-fdf98a07395e 20180928 google 2 2 0 0 5320032f-bf72-4e4e-a8c3-fdf98a07395e 20180924 null 0 0 0 0 5320032f-bf72-4e4e-a8c3-fdf98a07395e 20180927 null 0 0 0 0 5320032f-bf72-4e4e-a8c3-fdf98a07395e 20180923 null 0 0 0 0 5320032f-bf72-4e4e-a8c3-fdf98a07395e 20180925 google 2 2 0 0

Bot?  
Most of the records for the week are 0 uri 24 active hours.  profile_subsession_counter 159 is missing which could account for the short time on 9/23

In [69]:
# Look at 1 week of pings for client 0f8f
highat_c3 = ms_1week_raw.where("client_id like '%536100560f8f'").sort("submission_date_s3")
display(highat_c3.select(ms_1week_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 0 3 0.004166666666666667 59164 16.434444444444445 59171 160 20180923 2018-09-23T07:00:00.0+02:00 2018-09-23T07:00:00.0+02:00 daily 10 2 2 null 16880 null null release Windows_NT 10.0 17134 2018 2018-09-23T22:04:24.475Z null 20180923 20180830143136 62.0 release true true null 120 Mozilla false google Sun, 23 Sep 2018 22:53:47 GMT null null null null null null null false null DE Düsseldorf NW de List(Avast Antivirus) List(Avast Antivirus) List(Windows-Firewall) 5cde1c6b-4787-4e11-a965-e743770e05e0 a79bfb30-bcf9-4dcf-bdee-81e30782a112 null null null null List(default-theme@mozilla.org, false, Standard, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null null 42 96475fdb-3b7f-47ac-9280-7442eb1d4040 0 0 0.0 40 0.011111111111111112 28648 158 20180923 2018-09-20T19:00:00.0+02:00 2018-09-21T03:00:00.0+02:00 aborted-session 10 1 1 null 16880 null null release Windows_NT 10.0 17134 2018 2018-09-21T01:17:35.878Z null 20180923 20180830143136 62.0 release true true null 120 Mozilla false google Sun, 23 Sep 2018 05:53:03 GMT null null null null null null null null null DE Düsseldorf NW de List(Avast Antivirus) List(Avast Antivirus) List(Windows-Firewall) 458b4bb3-eb19-456b-b7af-df3cf1005f54 e4e17cea-8501-46e4-ae70-e0787a403f78 null null null null List(default-theme@mozilla.org, false, Standard, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null null 42 24867002-d213-4957-a55f-ec33601c03c4 0 4 0.005555555555555556 15770 4.3805555555555555 74941 161 20180924 2018-09-23T07:00:00.0+02:00 2018-09-24T00:00:00.0+02:00 shutdown 10 2 2 null 16880 null null release Windows_NT 10.0 17134 2018 2018-09-24T02:27:14.183Z null 20180924 20180830143136 62.0 release true true null 120 Mozilla false google Mon, 24 Sep 2018 02:27:15 GMT null null null null null null null null null DE Düsseldorf NW de List(Avast Antivirus) List(Avast Antivirus) List(Windows-Firewall) 5cde1c6b-4787-4e11-a965-e743770e05e0 2899099d-ed01-44cf-9b52-e52fb7671ba1 null null null null List(default-theme@mozilla.org, false, Standard, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null null 42 9382cf09-229b-4a5c-88bf-4fd2004d1a45 17 13994 19.43611111111111 70564 19.601111111111113 70566 162 20180924 2018-09-24T04:00:00.0+02:00 2018-09-24T04:00:00.0+02:00 daily 10 2 2 2 16880 null null release Windows_NT 10.0 17134 2018 2018-09-24T22:03:25.985Z null 20180924 20180830143136 62.0 release true true null 120 Mozilla false google Mon, 24 Sep 2018 22:32:29 GMT 23 204 null 2 2 null null false null DE Düsseldorf NW de List(Avast Antivirus) List(Avast Antivirus) List(Windows-Firewall) 026992d3-a1ce-4a68-ab3a-94c84c2ccd35 d352aa51-c62e-4a67-b326-fe2b915b9b0b null null null null List(default-theme@mozilla.org, false, Standard, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null null 42 f5b4d918-a2f3-4821-9425-99e1019cbbfd 0 17223 23.920833333333334 86404 24.00111111111111 156970 163 20180925 2018-09-24T04:00:00.0+0

In [70]:
# Summary stats for 1 week of client 0f8f
display(highat_c3['uri_count', 'active_ticks', 'active_tick_hrs', 'subsession_length', 'subsession_hours', 'session_length', 'submission_date_s3', 'country', 'city'].describe())

summary uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length submission_date_s3 country city count 9 9 9 9 9 9 9 9 9 mean 3.7777777777777777 11114.444444444445 15.436728395061728 64173.22222222222 17.825895061728396 209136.33333333334 2.0180925444444444E7 null null stddev 6.300352723811933 8398.36917370139 11.66440163014082 33527.89571303938 9.313304364733161 173099.87893626618 2.1858128414755935 null null min 0 0 0.0 40 0.011111111111111112 28648 20180923 DE Düsseldorf max 17 17238 23.941666666666666 86405 24.00138888888889 502590 20180929 DE Düsseldorf

Bot?  
7 very similar days

In [72]:
 # Look at 1 week of pings for client cdec
highat_c4 = ms_1week_raw.where("client_id like '%c86d7f20cdec'").sort("submission_date_s3")
display(highat_c4.select(ms_1week_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 0 17254 23.96388888888889 86405 24.00138888888889 4423681 197 20180923 2018-08-03T19:00:00.0+03:00 2018-09-23T00:00:00.0+03:00 daily 10 3 1 null 17358 null null release Windows_NT 6.1 7601 2017 2018-09-23T21:02:03.240Z null 20180923 20180704003137 61.0.1 release true true null 180 Mozilla true yandex-ru Sun, 23 Sep 2018 21:43:00 GMT null null null null null null null null null RU St Petersburg SPE ru null null null 9ba55397-c064-40e0-89c5-3a6d47ca3b8c 2efb7572-e331-4759-9e6b-db17c5158a07 null null null null List(default-theme@mozilla.org, false, По умолчанию, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(rollout-rdl -> active, rollout-release-61-tls-fallback-1-3 -> active) 42 5841c255-2000-4987-9291-bb84f513bed2 0 17255 23.96527777777778 86405 24.00138888888889 4510087 198 20180924 2018-08-03T19:00:00.0+03:00 2018-09-24T00:00:00.0+03:00 daily 10 3 1 null 17358 null null release Windows_NT 6.1 7601 2017 2018-09-24T21:02:08.960Z null 20180924 20180704003137 61.0.1 release true true null 180 Mozilla true yandex-ru Mon, 24 Sep 2018 21:43:00 GMT null null null null null null null null null RU St Petersburg SPE ru null null null 9ba55397-c064-40e0-89c5-3a6d47ca3b8c 555b2b66-3cc3-4af6-92c4-50eced2029ae null null null null List(default-theme@mozilla.org, false, По умолчанию, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(rollout-rdl -> active, rollout-release-61-tls-fallback-1-3 -> active) 42 a40b76d0-7998-4fc7-9643-a582ed7c1a40 0 17255 23.96527777777778 86405 24.00138888888889 4596493 199 20180925 2018-08-03T19:00:00.0+03:00 2018-09-25T00:00:00.0+03:00 daily 10 3 1 null 17358 null null release Windows_NT 6.1 7601 2017 2018-09-25T21:02:14.713Z null 20180925 20180704003137 61.0.1 release true true null 180 Mozilla true yandex-ru Tue, 25 Sep 2018 21:43:00 GMT null null null null null null null null null RU St Petersburg SPE ru null null null 9ba55397-c064-40e0-89c5-3a6d47ca3b8c 1f78da40-cffd-48d6-a302-db61ffd9da97 null null null null List(default-theme@mozilla.org, false, По умолчанию, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(rollout-rdl -> active, rollout-release-61-tls-fallback-1-3 -> active) 42 719a3114-4332-4744-a97a-d7175b3b772f 0 17255 23.96527777777778 86405 24.00138888888889 4682898 200 20180926 2018-08-03T19:00:00.0+03:00 2018-09-26T00:00:00.0+03:00 daily 10 3 1 null 17358 null null release Windows_NT 6.1 7601 2017 2018-09-26T21:02:20.456Z null 20180926 20180704003137 61.0.1 release true true null 180 Mozilla true yandex-ru Wed, 26 Sep 2018 21:43:00 GMT null null null null null null null null null RU St Petersburg SPE ru null null null 9ba55397-c064-40e0-89c5-3a6d47ca3b8c 2eb499f5-625b-4bc4-bf31-0c3cf7152c80 null null null null List(default-theme@mozilla.org, false, По умолчанию, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(rollout-rdl -> active, rollout-release-61-tls-fallback-1-3 -> active) 42 09

Bot?  
7 very similar days

In [74]:
# 1 week of pings for client 715e
highat_c5 = ms_1week_raw.where("client_id like '%94681e62715e'").sort("submission_date_s3")
display(highat_c5.select(ms_1week_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 0 17230 23.930555555555557 86407 24.001944444444444 3344105 172 20180923 2018-08-15T07:00:00.0-03:00 2018-09-22T00:00:00.0-03:00 daily 9 1 1 null 17653 null null release Windows_NT 10.0 17134 2018 2018-09-23T03:02:26.532Z null 20180923 20180807170231 61.0.2 release true true null -180 Mozilla true google Sun, 23 Sep 2018 03:58:05 GMT null null null null null null null null null BR ?? SC pt-BR List(Windows Defender Antivirus) List(Windows Defender Antivirus) List(Firewall do Windows) c1e1d574-79f6-4255-827b-e33048564bfa 335dd308-3412-48da-a743-f9192f8f4150 null null null null List(default-theme@mozilla.org, false, Padrão, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(rollout-release-61-tls-fallback-1-3 -> active, rollout-restart-manager-release-1481278 -> active) 42 ea80d92a-7ef9-442d-a2fb-eaf0fbf0109e 0 17228 23.927777777777777 86407 24.001944444444444 3430512 173 20180924 2018-08-15T07:00:00.0-03:00 2018-09-23T00:00:00.0-03:00 daily 9 1 1 null 17653 null null release Windows_NT 10.0 17134 2018 2018-09-24T03:02:33.190Z null 20180924 20180807170231 61.0.2 release true true null -180 Mozilla true google Mon, 24 Sep 2018 12:04:07 GMT null null null null null null null null null BR ?? SC pt-BR List(Windows Defender Antivirus) List(Windows Defender Antivirus) List(Firewall do Windows) c1e1d574-79f6-4255-827b-e33048564bfa 687c2d15-8dd0-468a-bfed-df4edaa0335c null null null null List(default-theme@mozilla.org, false, Padrão, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(rollout-release-61-tls-fallback-1-3 -> active, rollout-restart-manager-release-1481278 -> active) 42 51d127de-47fa-46d3-9a01-55496874d060 0 17230 23.930555555555557 86405 24.00138888888889 3516918 174 20180925 2018-08-15T07:00:00.0-03:00 2018-09-24T00:00:00.0-03:00 daily 9 1 1 null 17653 null null release Windows_NT 10.0 17134 2018 2018-09-25T03:02:39.368Z null 20180925 20180807170231 61.0.2 release true true null -180 Mozilla true google Tue, 25 Sep 2018 03:58:06 GMT null null null null null null null null null BR ?? SC pt-BR List(Windows Defender Antivirus) List(Windows Defender Antivirus) List(Firewall do Windows) c1e1d574-79f6-4255-827b-e33048564bfa 3eba5c21-89b6-4970-96b2-8ffe69b9b264 null null null null List(default-theme@mozilla.org, false, Padrão, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(rollout-release-61-tls-fallback-1-3 -> active, rollout-restart-manager-release-1481278 -> active) 42 ac88d7e4-5f5e-4e8a-a72d-e9225736d2be 0 17242 23.947222222222223 86406 24.001666666666665 3603325 175 20180926 2018-08-15T07:00:00.0-03:00 2018-09-25T00:00:00.0-03:00 daily 9 1 1 null 17653 null null release Windows_NT 10.0 17134 2018 2018-09-26T03:02:46.468Z null 20180926 20180807170231 61.0.2 release true true null -180 Mozilla true google Wed, 26 Sep 2018 03:58:05 GMT null null null null null null null null null BR ?? SC pt-BR List(Windows Defender Antivirus) List(Windows Defen

####Client ID used on multiple machines?

In [76]:
# check for duplicates of client id, submission date and profile_subsession_counter in 1 day of pings
ms_1day_dup = ms_1day_raw.groupBy('client_id', 'submission_date_s3', 'profile_subsession_counter')\
    .count()\
    .where(F.col('count') > 1).sort('client_id', 'submission_date_s3', 'profile_subsession_counter')
display(ms_1day_dup.select(['submission_date_s3', 'profile_subsession_counter', 'count']))

submission_date_s3 profile_subsession_counter count 20180925 2721 2 20180925 51 2 20180925 491 2 20180925 566 2 20180925 567 2 20180925 568 2 20180925 936 2 20180925 977 2 20180925 1122 2 20180925 1218 2 20180925 1219 2 20180925 1228 2 20180925 1627 2 20180925 1629 2 20180925 1852 2 20180925 2132 2 20180925 2275 2 20180925 2847 2 20180925 2848 2 20180925 2849 2 20180925 2850 2 20180925 3194 2 20180925 3195 2 20180925 3890 2 20180925 3891 2 20180925 8347 2 20180925 8348 2 20180925 8349 2 20180925 8350 2 20180925 432 2 20180925 2 2 20180925 1744 2 20180925 19 2 20180925 21 2 20180925 22 2 20180925 107 2 20180925 8 2 20180925 1 3 20180925 2 3 20180925 4 3 20180925 1 3 20180925 2 2 20180925 3 3 20180925 4 3 20180925 2 4 20180925 3 2 20180925 4 2 20180925 5 2 20180925 6 2 20180925 10 3 20180925 11 4 20180925 12 4 20180925 13 4 20180925 14 3 20180925 15 3 20180925 16 2 20180925 17 2 20180925 18 2 20180925 19 2 20180925 20 2 20180925 27 2 20180925 29 2 20180925 1 2 20180925 423 2 20180925 7 2 20180925 34 3 20180925 35 2 20180925 36 2 20180925 37 4 20180925 38 4 20180925 40 4 20180925 41 4 20180925 42 3 20180925 43 4 20180925 44 3 20180925 47 2 20180925 48 3 20180925 49 2 20180925 50 4 20180925 51 4 20180925 52 6 20180925 53 2 20180925 54 2 20180925 57 2 20180925 59 2 20180925 61 2 20180925 63 4 20180925 64 2 20180925 65 2 20180925 67 2 20180925 69 3 20180925 70 2 20180925 97 2 20180925 455 2 20180925 401 2 20180925 121 17 20180925 32 2 20180925 35 9 20180925 36 12 20180925 1293 2 20180925 2795 2 20180925 688 2 20180925 150 2 20180925 87 2 20180925 34 2 20180925 55 3 20180925 72 2 20180925 102 2 20180925 507 2 20180925 508 2 20180925 509 2 20180925 817 2 20180925 3157 2 20180925 406 4 20180925 407 2 20180925 408 2 20180925 15 3 20180925 16 3 20180925 17 5 20180925 18 9 20180925 19 7 20180925 20 4 20180925 21 5 20180925 10 2 20180925 11 2 20180925 12 2 20180925 13 2 20180925 17 2 20180925 157 2 20180925 3299 2 20180925 2112 2 20180925 2113 2 20180925 667 2 20180925 1687 2 20180925 14 5 20180925 15 4 20180925 16 3 20180925 17 5 20180925 18 2 20180925 68 2 20180925 69 2 20180925 302 2 20180925 28 2 20180925 2 3 20180925 1 4 20180925 2 3 20180925 90 2 20180925 91 2 20180925 16 2 20180925 1924 2 20180925 41 2 20180925 5829 2 20180925 5830 2 20180925 5831 2 20180925 697 2 20180925 366 2 20180925 367 2 20180925 368 2 20180925 369 2 20180925 1078 2 20180925 2 2 20180925 3 2 20180925 5 2 20180925 8 2 20180925 2695 2 20180925 262 2 20180925 121 2 20180925 2 2 20180925 750 3 20180925 1 2 20180925 5 2 20180925 6 2 20180925 1 6 20180925 5 7 20180925 6 4 20180925 3 3 20180925 4 3 20180925 541 2 20180925 6 4 20180925 7 6 20180925 8 5 20180925 9 2 20180925 1415 2 20180925 1798 2 20180925 434 2 20180925 236 2 20180925 40 2 20180925 41 2 20180925 301 2 20180925 218 2 20180925 1 4 20180925 1 2 20180925 17 2 20180925 18 2 20180925 19 2 20180925 1246 2 20180925 4 2 20180925 1381 2 20180925 107 2 20180925 30 2 20180925 389 2 20180925 2 2 20180925 3 2 20180925 996 2 20180925 3067 2 20180925 1378 3 20180925 1687 2 20180925 67 2 20180925 7 3 20180925 8 3 20180925 9 3 20180925 121 2 20180925 503 2 20180925 549 2 20180925 2362 2 20180925 1 5 20180925 659 2 20180925 1832 2 20180925 1424 2 20180925 60 2 20180925 61 2 20180925 65 2 20180925 1 2 20180925 56 2 20180925 1870 2 20180925 1871 2 20180925 614 2 20180925 3 4 20180925 6 3 20180925 9 3 20180925 427 2 20180925 1931 2 20180925 11 2 20180925 215 2 20180925 1126 2 20180925 72 4 20180925 122 2 20180925 164 2 20180925 1051 2 20180925 16 2 20180925 4890 2 20180925 11 9 20180925 12 7 20180925 13 3 20180925 1 2 20180925 2 2 20180925 15 2 20180925 10 2 20180925 2690 2 20180925 6 4 20180925 7 3 20180925 392 2 20180925 393 7 20180925 394 5 20180925 395 4 20180925 396 6 20180925 397 7 20180925 398 5 20180925 399 3 20180925 142 2 20180925 42 2 20180925 52 2 20180925 53 2 20180925 54 2 20180925 55 2 20180925 56 2 20180925 58 2 20180925 128 2 20180925 43 2 20180925 118 2 20180925 2097 2 20180925 1 2 20180925 2 2 20180925 9

In [77]:
# Summary stats for duplicate client_id and profile_subsession_counter in raw pings in 1 day
ms_1day_dup.select(['submission_date_s3', 'profile_subsession_counter', 'count']).describe().show()

+-------+------------------+--------------------------+-----------------+
summary|submission_date_s3|profile_subsession_counter| count|
+-------+------------------+--------------------------+-----------------+
 count| 69894| 69894| 69894|
 mean| 2.0180925E7| 19961.26235442241|7.315391879131256|
 stddev| 0.0| 21241.92582065114|9.816503903811348|
 min| 20180925| 1| 2|
 max| 20180925| 87308| 1157|
+-------+------------------+--------------------------+-----------------+

There are still a lot of these duplicate client_id and profile_subsession_counter in records with at least 1 uri.

In [79]:
# Get 1day raw where uri > 1
ms_1day_1uri = ms_1day_raw.where("uri_count >= 1")
# check for duplicates of client id, submission date and profile_subsession_counter in 1 day of pings
ms_1day_1uri_dup = ms_1day_1uri.groupBy('client_id', 'submission_date_s3', 'profile_subsession_counter')\
    .count()\
    .where(F.col('count') > 1).sort('client_id', 'submission_date_s3', 'profile_subsession_counter')
# Summary stats for duplicate client_id and profile_subsession_counter in 1 day
ms_1day_1uri_dup.select(['submission_date_s3', 'profile_subsession_counter', 'count']).describe().show()

+-------+------------------+--------------------------+------------------+
summary|submission_date_s3|profile_subsession_counter| count|
+-------+------------------+--------------------------+------------------+
 count| 16236| 16236| 16236|
 mean| 2.0180925E7| 576.3824833702882| 3.150960827790096|
 stddev| 0.0| 1288.4452106004849|6.7010932047892195|
 min| 20180925| 1| 2|
 max| 20180925| 38115| 603|
+-------+------------------+--------------------------+------------------+

Look at client with the highest number of duplicate profile_subsession_counters in 1 day

In [81]:
# Look at client with highest number of duplicates
dup_high = ms_1day_dup.where("count = 1157")
display(dup_high.select(['submission_date_s3', 'profile_subsession_counter', 'count']))

submission_date_s3 profile_subsession_counter count 20180925 17 1157

The following client has a lot of records in one day, some Windows some Linux.  Many of them (like profile_subsession_counter = 15) look like duplicate entries but they have different client_submission_dates.  Would private browsing cause all 0s and nulls?

In [83]:
# Show all the pings in a day for client 038e
dup_c = ms_1day_raw.where("client_id like '%223eb500038e'").sort("submission_date_s3", "profile_subsession_counter")
display(dup_c.select(ms_1day_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date subsession_counter reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 0 0 0.0 10 0.002777777777777778 13 1 20180925 2018-09-25T00:00:00.0-04:00 2018-09-25T00:00:00.0-04:00 1 shutdown 0 1 1 null 17386 null null esr Linux 4.9.0 null null 2018-09-25T20:00:42.103Z null 20180925 20170627155318 52.2.1 esr false false null -240 Mozilla false google Tue, 25 Sep 2018 20:01:49 GMT null null null null null null null null null BR Palmas TO pt-BR null null null 9f2fa1a0-0839-4abd-914d-c60fe658b620 e58fa864-e6fe-4776-a32c-7fce28d02b50 false null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Padrão, false, false, 52.2.1, 4, null, false, false, 17345, 17345, null, null, null, null) null null 42 515a9021-0298-4c75-bc98-7e3e99aaf644 0 0 0.0 137 0.03805555555555556 139 4 20180925 2018-09-21T00:00:00.0-04:00 2018-09-21T00:00:00.0-04:00 1 shutdown 0 1 1 null 17386 null null esr Linux 4.9.0 null null 2018-09-21T17:47:09.612Z null 20180925 20170627155318 52.2.1 esr false false null -240 Mozilla false google Tue, 25 Sep 2018 13:00:25 GMT null null null null null null null null null BR Palmas TO pt-BR null null null ab12b865-59f1-4e05-a289-0238117dc394 cfb1a5e0-0a93-41e3-933c-56cd7f9a4dcb false null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Padrão, false, false, 52.2.1, 4, null, false, false, 17345, 17345, null, null, null, null) null null 42 746474a1-9aa7-4b12-b4c0-5440fd4178d6 0 0 0.0 25 0.006944444444444444 26 5 20180925 2018-09-21T00:00:00.0-04:00 2018-09-21T00:00:00.0-04:00 1 shutdown 0 1 1 null 17386 null null esr Linux 4.9.0 null null 2018-09-21T17:47:39.011Z null 20180925 20170627155318 52.2.1 esr false false null -240 Mozilla false google Tue, 25 Sep 2018 13:00:25 GMT null null null null null null null null null BR Palmas TO pt-BR null null null 4a0ac806-174a-413a-bd83-36f945439dfd 9ddb6e7b-d3b8-4d80-891f-14bd3159f8f3 false null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Padrão, false, false, 52.2.1, 4, null, false, false, 17345, 17345, null, null, null, null) null null 42 49143c81-08bd-4fe5-91d6-12a95943b505 0 0 0.0 127 0.035277777777777776 129 9 20180925 2018-07-23T00:00:00.0-04:00 2018-07-23T00:00:00.0-04:00 1 shutdown 6 1 1 null 17386 null null esr Linux 4.9.0 null null 2018-07-23T17:20:54.481Z null 20180925 20170627155318 52.2.1 esr false false null -240 Mozilla false google Tue, 25 Sep 2018 19:40:04 GMT null null null null null null null null null BR Palmas TO pt-BR null null null 9e08250a-9a4a-4647-924c-d58f8e9447af e2b311b1-527b-4a45-83f8-c51944831c2d false null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Padrão, false, false, 52.2.1, 4, null, false, false, 15995, 17345, null, null, null, null) null null 42 3053b2da-0019-453d-ae0a-8ae243cc7176 0 0 0.0 127 0.035277777777777776 129 9 20180925 2018-07-23T00:00:00.0-04:00 2018-07-23T00:00:00.0-04:00 1 shutdown 6 1 1 null 17386 null null esr Linux 4.9.0 null null 2018-07-23T17:20:54.481Z null 20180925 20170627155318 52.2.1 esr false false null -240 Mozilla false google

In [84]:
# Show summary stats for client 038e with duplicate profile_subsession_counters in a day
display(dup_c.select(ms_1week_raw_cols).describe())

summary uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel active_experiment_branch timezone_offset vendor default_search_engine client_submission_date places_bookmarks_count places_pages_count tab_event_count window_event_count errors_collected_count media_page_count country city geo_subdivision1 locale session_id subsession_id sync_count_desktop sync_count_mobile sample_id document_id count 3541 3541 3541 3541 3541 3541 3541 3541 3541 3541 3541 3541 3535 3535 0 3541 0 2 3541 3541 3541 0 2674 3541 0 3541 3541 3541 3541 0 3541 3541 3540 3541 1241 1241 1082 577 0 0 3541 3541 3541 3541 3541 3541 0 0 3541 3541 mean 0.0 0.0 0.0 3164.730019768427 0.8790916721578962 5575.871787630613 23.15221688788478 2.0180925E7 null null null 6.0237221123976274 1.4424328147100425 1.2503536067892504 null 17386.0 null 2.0170627155318E13 null null 6.1001495886313 null 2016.1761406133135 null null 2.0180925E7 2.017063279999971E13 null null null -195.5888167184411 null null null 8.724415793714746 9.596293311845287 3.3059149722735675 4.412478336221837 null null null null null null null null null null 42.0 null stddev 0.0 0.0 0.0 19352.877491108324 5.375799303085644 42885.59454582732 12.42833643886792 0.0 null null null 0.2978298828876097 0.8837390144543735 0.5547135721610276 null 0.0 null 0.0 null null 0.005468686651089214 null 1.105040279075722 null null 0.0 2.3747946534039634E8 null null null 26.315648698527394 null null null 1.551209258114467 1.731758138246403 4.189514039295673 4.664402381479623 null null null null null null null null null null 0.0 null min 0 0 0.0 0 0.0 3 1 20180925 2018-05-18T00:00:00.0-03:00 2018-05-18T00:00:00.0-03:00 aborted-session 0 0 0 null 17386 null 20170627155318 esr Linux 3.16.0 null 2012 2018-05-18T13:26:45.251Z null 20180925 20170627155318 52.2.1 esr null -240 Mozilla google Tue, 25 Sep 2018 00:17:19 GMT 0 0 1 1 null null BR Aracaju AL pt-BR 00019b5e-3619-431b-a799-a6970382c7a5 0027bc0b-472e-4c16-b0f7-a635304043ff null null 42 00052d24-9b79-432c-88dd-33531047233b max 0 0 0.0 1032500 286.80555555555554 1063359 60 20180925 2018-09-25T00:00:00.0-04:00 2018-09-25T00:00:00.0-04:00 shutdown 8 33 9 null 17386 null 20170627155318 esr Windows_NT 6.3 null 2018 2018-09-25T23:15:43.973Z null 20180925 20180621064021 52.9.0 esr null -180 Mozilla google Tue, 25 Sep 2018 23:58:12 GMT 9 10 46 46 null null BR Vitória TO pt-BR ffef43b2-7b51-4ee3-b7cc-68b1b4f38606 fffadf5c-ac94-4fdb-986e-ae015972d973 null null 42 fffc4b6c-a114-45a2-a383-e68b2b79c411

Lots of different users using this client_id  
profile_subsession_counter reused many times on one day, different operating systems, in many different locations

In [86]:
# Show duplicate counts by profile_subsession_counter for client 038e over the day
dup_c_count = dup_c.groupBy("submission_date_s3", "profile_subsession_counter") \
  .agg(F.count(F.lit(1)).alias("num_records"), F.min("os"))
display(dup_c_count)

submission_date_s3 profile_subsession_counter num_records min(os) 20180925 1 1 Linux 20180925 4 1 Linux 20180925 5 1 Linux 20180925 9 28 Linux 20180925 10 27 Linux 20180925 11 26 Linux 20180925 15 432 Windows_NT 20180925 16 173 Windows_NT 20180925 17 1157 Windows_NT 20180925 18 447 Windows_NT 20180925 19 186 Windows_NT 20180925 20 102 Windows_NT 20180925 21 56 Windows_NT 20180925 22 56 Linux 20180925 23 57 Linux 20180925 24 27 Linux 20180925 25 19 Linux 20180925 26 10 Linux 20180925 27 9 Linux 20180925 28 7 Linux 20180925 29 10 Linux 20180925 30 18 Linux 20180925 31 17 Linux 20180925 32 16 Linux 20180925 33 16 Linux 20180925 34 17 Linux 20180925 35 21 Linux 20180925 36 19 Linux 20180925 37 21 Linux 20180925 38 25 Linux 20180925 39 19 Linux 20180925 40 20 Linux 20180925 41 21 Linux 20180925 42 23 Linux 20180925 43 25 Linux 20180925 44 26 Linux 20180925 45 21 Linux 20180925 46 23 Linux 20180925 47 25 Linux 20180925 48 24 Linux 20180925 49 24 Linux 20180925 50 28 Linux 20180925 51 23 Linux 20180925 52 26 Linux 20180925 53 17 Linux 20180925 54 29 Linux 20180925 55 30 Linux 20180925 56 28 Linux 20180925 57 26 Linux 20180925 58 27 Linux 20180925 59 26 Linux 20180925 60 28 Linux

In [87]:
# Show countries for client 038e
dup_c.select("country",  "city").distinct().show()

+-------+--------------+
country| city|
+-------+--------------+
 BR| Campo Grande|
 BR| São Paulo|
 BR| Aracaju|
 BR| Teresina|
 BR| Porto Alegre|
 BR| Salvador|
 BR| João Pessoa|
 BR| Goiânia|
 BR|Rio de Janeiro|
 BR| Palmas|
 BR| Natal|
 BR| São Luís|
 BR| Maceió|
 BR| Brasília|
 BR| Curitiba|
 BR| Santana|
 BR| Belém|
 BR| Recife|
 BR| Vitória|
 BR|Belo Horizonte|
+-------+--------------+
only showing top 20 rows

In [88]:
# Look at profile_subsession_counter 15 for client 038e
dup_c15 = dup_c.where("profile_subsession_counter = 15")
display(dup_c15.select(ms_1day_raw_cols).describe())

summary uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date subsession_counter reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel active_experiment_branch timezone_offset vendor default_search_engine client_submission_date places_bookmarks_count places_pages_count tab_event_count window_event_count errors_collected_count media_page_count country city geo_subdivision1 locale session_id subsession_id sync_count_desktop sync_count_mobile sample_id document_id count 432 432 432 432 432 432 432 432 432 432 432 432 432 432 432 0 432 0 1 432 432 432 0 432 432 0 432 432 432 432 0 432 432 432 432 259 259 111 56 0 0 432 432 432 432 432 432 0 0 432 432 mean 0.0 0.0 0.0 5267.305555555556 1.4631404320987644 5271.506944444444 15.0 2.0180925E7 null null 1.0 null 6.00462962962963 1.3148148148148149 1.1574074074074074 null 17386.0 null 2.0170627155318E13 null null 6.099999999999951 null 2016.3055555555557 null null 2.0180925E7 2.017065028936592E13 null null null -180.13888888888889 null null null 9.0 9.972972972972974 2.2882882882882885 2.517857142857143 null null null null null null null null null null 42.0 null stddev 0.0 0.0 0.0 49782.62499857402 13.82850694404834 49782.55396185644 0.0 0.0 null null 0.0 null 0.06796240158764906 0.5922648831772633 0.37711905933033973 null 0.0 null NaN null null 0.0 null 0.8338358886794093 null null 0.0 4.808321566611328E8 null null null 2.8867513459481295 null null null 0.0 0.1624761259840059 3.2596357503907125 2.280279659312718 null null null null null null null null null null 0.0 null min 0 0 0.0 3 8.333333333333334E-4 4 15 20180925 2018-05-18T00:00:00.0-03:00 2018-05-18T00:00:00.0-03:00 1 aborted-session 6 1 1 null 17386 null 20170627155318 esr Windows_NT 6.1 null 2014 2018-05-18T13:52:37.902Z null 20180925 20170627155318 52.2.1 esr null -240 Mozilla google Tue, 25 Sep 2018 10:21:28 GMT 9 9 1 1 null null BR Brasília DF pt-BR 0036988a-33c7-49d5-9b83-059010cd32cf 0050ec85-977a-4929-b42f-413b2b180761 null null 42 00465e78-d823-4c71-976f-d02cf66814db max 0 0 0.0 1032500 286.80555555555554 1032504 15 20180925 2018-09-25T00:00:00.0-03:00 2018-09-25T00:00:00.0-03:00 1 shutdown 7 7 3 null 17386 null 20170627155318 esr Windows_NT 6.1 null 2018 2018-09-25T18:26:19.294Z null 20180925 20180621064021 52.9.0 esr null -180 Mozilla google Tue, 25 Sep 2018 21:57:12 GMT 9 10 27 12 null null BR Teresina SP pt-BR fe6ea90c-0059-45be-8781-599f85707864 ff0e2de0-5a66-4a6a-9e8c-034e627dcb83 null null 42 fffc4b6c-a114-45a2-a383-e68b2b79c411

Client 7728 has lots of identical looking rows for profile_subsession_counter = 35 and 36 all on the same day. Different client_submission_dates, but same session_id and subsession_id.  ??

In [90]:
# profile_subsession_counter 35 for client 7728
dup_c35 = ms_1day_raw.where("client_id like'%4cb365627728' and profile_subsession_counter = 35").sort("submission_date_s3", "profile_subsession_counter")
display(dup_c35.select(ms_1day_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date subsession_counter reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 56 114 0.15833333333333333 24545 6.8180555555555555 24546 35 20180925 2018-09-21T09:00:00.0+03:00 2018-09-21T09:00:00.0+03:00 1 shutdown 9 1 1 1 17714 null null release Windows_NT 6.3 9600 2018 2018-09-21T13:23:33.307Z null 20180925 20180807170231 61.0.2 release true true null 180 Mozilla false yandex-ru Tue, 25 Sep 2018 14:09:03 GMT 7 214 null null null null null false null RU Moscow MOW ru null null null 255ebc9d-d0f7-43c9-9272-59dbfd5d285f a2da1015-4ee1-4dab-96ca-f796cfbe9366 null null null null List(default-theme@mozilla.org, false, По умолчанию, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(pref-hotfix-tls-13-avast-rollback -> default) 42 89e66335-2302-4c91-a03b-14588c98e835 56 114 0.15833333333333333 24545 6.8180555555555555 24546 35 20180925 2018-09-21T09:00:00.0+03:00 2018-09-21T09:00:00.0+03:00 1 shutdown 9 1 1 1 17714 null null release Windows_NT 6.3 9600 2018 2018-09-21T13:23:33.307Z null 20180925 20180807170231 61.0.2 release true true null 180 Mozilla false yandex-ru Tue, 25 Sep 2018 14:23:16 GMT 7 214 null null null null null false null RU Moscow MOW ru null null null 255ebc9d-d0f7-43c9-9272-59dbfd5d285f a2da1015-4ee1-4dab-96ca-f796cfbe9366 null null null null List(default-theme@mozilla.org, false, По умолчанию, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(pref-hotfix-tls-13-avast-rollback -> default) 42 89e66335-2302-4c91-a03b-14588c98e835 56 114 0.15833333333333333 24545 6.8180555555555555 24546 35 20180925 2018-09-21T09:00:00.0+03:00 2018-09-21T09:00:00.0+03:00 1 shutdown 9 1 1 1 17714 null null release Windows_NT 6.3 9600 2018 2018-09-21T13:23:33.307Z null 20180925 20180807170231 61.0.2 release true true null 180 Mozilla false yandex-ru Tue, 25 Sep 2018 14:11:12 GMT 7 214 null null null null null false null RU Moscow MOW ru null null null 255ebc9d-d0f7-43c9-9272-59dbfd5d285f a2da1015-4ee1-4dab-96ca-f796cfbe9366 null null null null List(default-theme@mozilla.org, false, По умолчанию, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(pref-hotfix-tls-13-avast-rollback -> default) 42 89e66335-2302-4c91-a03b-14588c98e835 56 114 0.15833333333333333 24545 6.8180555555555555 24546 35 20180925 2018-09-21T09:00:00.0+03:00 2018-09-21T09:00:00.0+03:00 1 shutdown 9 1 1 1 17714 null null release Windows_NT 6.3 9600 2018 2018-09-21T13:23:33.307Z null 20180925 20180807170231 61.0.2 release true true null 180 Mozilla false yandex-ru Tue, 25 Sep 2018 14:07:02 GMT 7 214 null null null null null false null RU Moscow MOW ru null null null 255ebc9d-d0f7-43c9-9272-59dbfd5d285f a2da1015-4ee1-4dab-96ca-f796cfbe9366 null null null null List(default-theme@mozilla.org, false, По умолчанию, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(pref-hotfix-tls-13-avast-rollback -> default) 42 89e66335-2302-4c91-a03b-14588c98e835 56 114 0.15833333333333333 24545 6.8180555555555555 24546 35 20180925 2018-09-

In [91]:
# profile_subsession_counter 35 for client 7728
display(dup_c35.select(ms_1day_raw_cols).describe())

summary uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date subsession_counter reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel active_experiment_branch timezone_offset vendor default_search_engine client_submission_date places_bookmarks_count places_pages_count tab_event_count window_event_count errors_collected_count media_page_count country city geo_subdivision1 locale session_id subsession_id sync_count_desktop sync_count_mobile sample_id document_id count 9 9 9 9 9 9 9 9 9 9 9 9 9 9 9 9 9 0 0 9 9 9 9 9 9 0 9 9 9 9 0 9 9 9 9 9 9 0 0 0 0 9 9 9 9 9 9 0 0 9 9 mean 56.0 114.0 0.15833333333333333 24545.0 6.818055555555555 24546.0 35.0 2.0180925E7 null null 1.0 null 9.0 1.0 1.0 1.0 17714.0 null null null null 6.299999999999999 9600.0 2018.0 null null 2.0180925E7 2.0180807170231E13 null null null 180.0 null null null 7.0 214.0 null null null null null null null null null null null null 42.0 null stddev 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 null null 0.0 null 0.0 0.0 0.0 0.0 0.0 null null null null 0.0 0.0 0.0 null null 0.0 0.0 null null null 0.0 null null null 0.0 0.0 null null null null null null null null null null null null 0.0 null min 56 114 0.15833333333333333 24545 6.8180555555555555 24546 35 20180925 2018-09-21T09:00:00.0+03:00 2018-09-21T09:00:00.0+03:00 1 shutdown 9 1 1 1 17714 null null release Windows_NT 6.3 9600 2018 2018-09-21T13:23:33.307Z null 20180925 20180807170231 61.0.2 release null 180 Mozilla yandex-ru Tue, 25 Sep 2018 14:05:17 GMT 7 214 null null null null RU Moscow MOW ru 255ebc9d-d0f7-43c9-9272-59dbfd5d285f a2da1015-4ee1-4dab-96ca-f796cfbe9366 null null 42 89e66335-2302-4c91-a03b-14588c98e835 max 56 114 0.15833333333333333 24545 6.8180555555555555 24546 35 20180925 2018-09-21T09:00:00.0+03:00 2018-09-21T09:00:00.0+03:00 1 shutdown 9 1 1 1 17714 null null release Windows_NT 6.3 9600 2018 2018-09-21T13:23:33.307Z null 20180925 20180807170231 61.0.2 release null 180 Mozilla yandex-ru Tue, 25 Sep 2018 15:05:11 GMT 7 214 null null null null RU Moscow MOW ru 255ebc9d-d0f7-43c9-9272-59dbfd5d285f a2da1015-4ee1-4dab-96ca-f796cfbe9366 null null 42 89e66335-2302-4c91-a03b-14588c98e835

In [92]:
# profile_subsession_counter 36 for client 7728
dup_c36 = ms_1day_raw.where("client_id like '%4cb365627728' and profile_subsession_counter = 36").sort("submission_date_s3", "profile_subsession_counter")
display(dup_c36.select(ms_1day_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date subsession_counter reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 57 60 0.08333333333333333 8586 2.385 8587 36 20180925 2018-09-24T09:00:00.0+03:00 2018-09-24T09:00:00.0+03:00 1 shutdown 9 1 1 1 17714 null null release Windows_NT 6.3 9600 2018 2018-09-24T08:38:12.075Z null 20180925 20180807170231 61.0.2 release true true null 180 Mozilla false yandex-ru Tue, 25 Sep 2018 14:11:12 GMT 7 214 null null null null null false null RU Moscow MOW ru null null null 0c807d17-ac8d-49b8-8dcf-a142574caceb c27446c6-966a-45d9-ad7b-3a95700945cf null null null null List(default-theme@mozilla.org, false, По умолчанию, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(pref-hotfix-tls-13-avast-rollback -> default) 42 9669667c-7871-42d4-98ef-a6cbf76971c6 57 60 0.08333333333333333 8586 2.385 8587 36 20180925 2018-09-24T09:00:00.0+03:00 2018-09-24T09:00:00.0+03:00 1 shutdown 9 1 1 1 17714 null null release Windows_NT 6.3 9600 2018 2018-09-24T08:38:12.075Z null 20180925 20180807170231 61.0.2 release true true null 180 Mozilla false yandex-ru Tue, 25 Sep 2018 14:07:02 GMT 7 214 null null null null null false null RU Moscow MOW ru null null null 0c807d17-ac8d-49b8-8dcf-a142574caceb c27446c6-966a-45d9-ad7b-3a95700945cf null null null null List(default-theme@mozilla.org, false, По умолчанию, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(pref-hotfix-tls-13-avast-rollback -> default) 42 9669667c-7871-42d4-98ef-a6cbf76971c6 57 60 0.08333333333333333 8586 2.385 8587 36 20180925 2018-09-24T09:00:00.0+03:00 2018-09-24T09:00:00.0+03:00 1 shutdown 9 1 1 1 17714 null null release Windows_NT 6.3 9600 2018 2018-09-24T08:38:12.075Z null 20180925 20180807170231 61.0.2 release true true null 180 Mozilla false yandex-ru Tue, 25 Sep 2018 15:05:11 GMT 7 214 null null null null null false null RU Moscow MOW ru null null null 0c807d17-ac8d-49b8-8dcf-a142574caceb c27446c6-966a-45d9-ad7b-3a95700945cf null null null null List(default-theme@mozilla.org, false, По умолчанию, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(pref-hotfix-tls-13-avast-rollback -> default) 42 9669667c-7871-42d4-98ef-a6cbf76971c6 57 60 0.08333333333333333 8586 2.385 8587 36 20180925 2018-09-24T09:00:00.0+03:00 2018-09-24T09:00:00.0+03:00 1 shutdown 9 1 1 1 17714 null null release Windows_NT 6.3 9600 2018 2018-09-24T08:38:12.075Z null 20180925 20180807170231 61.0.2 release true true null 180 Mozilla false yandex-ru Tue, 25 Sep 2018 14:39:18 GMT 7 214 null null null null null false null RU Moscow MOW ru null null null 0c807d17-ac8d-49b8-8dcf-a142574caceb c27446c6-966a-45d9-ad7b-3a95700945cf null null null null List(default-theme@mozilla.org, false, По умолчанию, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(pref-hotfix-tls-13-avast-rollback -> default) 42 9669667c-7871-42d4-98ef-a6cbf76971c6 57 60 0.08333333333333333 8586 2.385 8587 36 20180925 2018-09-24T09:00:00.0+03:00 2018-09-24T09:00:00.0+03:00 1 shutdown 9 1 1 1 17714 null nu

In [93]:
# profile_subsession_counter 36 for client 7728
display(dup_c36.select(ms_1day_raw_cols).describe())

summary uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date subsession_counter reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel active_experiment_branch timezone_offset vendor default_search_engine client_submission_date places_bookmarks_count places_pages_count tab_event_count window_event_count errors_collected_count media_page_count country city geo_subdivision1 locale session_id subsession_id sync_count_desktop sync_count_mobile sample_id document_id count 12 12 12 12 12 12 12 12 12 12 12 12 12 12 12 12 12 0 0 12 12 12 12 12 12 0 12 12 12 12 0 12 12 12 12 12 12 0 0 0 0 12 12 12 12 12 12 0 0 12 12 mean 57.0 60.0 0.08333333333333333 8586.0 2.3849999999999993 8587.0 36.0 2.0180925E7 null null 1.0 null 9.0 1.0 1.0 1.0 17714.0 null null null null 6.299999999999998 9600.0 2018.0 null null 2.0180925E7 2.0180807170231E13 null null null 180.0 null null null 7.0 214.0 null null null null null null null null null null null null 42.0 null stddev 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 null null 0.0 null 0.0 0.0 0.0 0.0 0.0 null null null null 0.0 0.0 0.0 null null 0.0 0.0 null null null 0.0 null null null 0.0 0.0 null null null null null null null null null null null null 0.0 null min 57 60 0.08333333333333333 8586 2.385 8587 36 20180925 2018-09-24T09:00:00.0+03:00 2018-09-24T09:00:00.0+03:00 1 shutdown 9 1 1 1 17714 null null release Windows_NT 6.3 9600 2018 2018-09-24T08:38:12.075Z null 20180925 20180807170231 61.0.2 release null 180 Mozilla yandex-ru Tue, 25 Sep 2018 14:05:17 GMT 7 214 null null null null RU Moscow MOW ru 0c807d17-ac8d-49b8-8dcf-a142574caceb c27446c6-966a-45d9-ad7b-3a95700945cf null null 42 9669667c-7871-42d4-98ef-a6cbf76971c6 max 57 60 0.08333333333333333 8586 2.385 8587 36 20180925 2018-09-24T09:00:00.0+03:00 2018-09-24T09:00:00.0+03:00 1 shutdown 9 1 1 1 17714 null null release Windows_NT 6.3 9600 2018 2018-09-24T08:38:12.075Z null 20180925 20180807170231 61.0.2 release null 180 Mozilla yandex-ru Tue, 25 Sep 2018 15:05:11 GMT 7 214 null null null null RU Moscow MOW ru 0c807d17-ac8d-49b8-8dcf-a142574caceb c27446c6-966a-45d9-ad7b-3a95700945cf null null 42 9669667c-7871-42d4-98ef-a6cbf76971c6

What's going on with client 7728 over a week?  
Lots of duplicate profile_subsession_counters over different days.  Records looks like copies except for client_submission_date

In [95]:
# Look at a week of pings for client 7728
dup_c1 = ms_1week_raw.where("client_id like '%4cb365627728'").sort("submission_date_s3", "profile_subsession_counter")
display(dup_c1.select(ms_1week_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 58 89 0.12361111111111112 68565 19.045833333333334 267797 33 20180924 2018-09-14T16:00:00.0+03:00 2018-09-17T00:00:00.0+03:00 shutdown 9 4 2 1 17714 null null release Windows_NT 6.3 9600 2018 2018-09-17T16:04:20.845Z null 20180924 20180807170231 61.0.2 release true true null 180 Mozilla false yandex-ru Mon, 24 Sep 2018 07:20:07 GMT 7 211 null 2 2 null null null null RU Moscow MOW ru null null null 73444389-6876-44ac-b394-d7e010111f63 9149240e-20d6-48e6-8c35-f7a1f460f09e null null null null List(default-theme@mozilla.org, false, По умолчанию, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(pref-hotfix-tls-13-avast-rollback -> default) 42 6728fb62-c2b9-46cc-91c1-f02208412434 58 89 0.12361111111111112 68565 19.045833333333334 267797 33 20180924 2018-09-14T16:00:00.0+03:00 2018-09-17T00:00:00.0+03:00 shutdown 9 4 2 1 17714 null null release Windows_NT 6.3 9600 2018 2018-09-17T16:04:20.845Z null 20180924 20180807170231 61.0.2 release true true null 180 Mozilla false yandex-ru Mon, 24 Sep 2018 07:16:04 GMT 7 211 null 2 2 null null null null RU Moscow MOW ru null null null 73444389-6876-44ac-b394-d7e010111f63 9149240e-20d6-48e6-8c35-f7a1f460f09e null null null null List(default-theme@mozilla.org, false, По умолчанию, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(pref-hotfix-tls-13-avast-rollback -> default) 42 6728fb62-c2b9-46cc-91c1-f02208412434 58 89 0.12361111111111112 68565 19.045833333333334 267797 33 20180924 2018-09-14T16:00:00.0+03:00 2018-09-17T00:00:00.0+03:00 shutdown 9 4 2 1 17714 null null release Windows_NT 6.3 9600 2018 2018-09-17T16:04:20.845Z null 20180924 20180807170231 61.0.2 release true true null 180 Mozilla false yandex-ru Mon, 24 Sep 2018 06:32:55 GMT 7 211 null 2 2 null null null null RU Moscow MOW ru null null null 73444389-6876-44ac-b394-d7e010111f63 9149240e-20d6-48e6-8c35-f7a1f460f09e null null null null List(default-theme@mozilla.org, false, По умолчанию, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(pref-hotfix-tls-13-avast-rollback -> default) 42 6728fb62-c2b9-46cc-91c1-f02208412434 58 89 0.12361111111111112 68565 19.045833333333334 267797 33 20180924 2018-09-14T16:00:00.0+03:00 2018-09-17T00:00:00.0+03:00 shutdown 9 4 2 1 17714 null null release Windows_NT 6.3 9600 2018 2018-09-17T16:04:20.845Z null 20180924 20180807170231 61.0.2 release true true null 180 Mozilla false yandex-ru Mon, 24 Sep 2018 07:14:02 GMT 7 211 null 2 2 null null null null RU Moscow MOW ru null null null 73444389-6876-44ac-b394-d7e010111f63 9149240e-20d6-48e6-8c35-f7a1f460f09e null null null null List(default-theme@mozilla.org, false, По умолчанию, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(pref-hotfix-tls-13-avast-rollback -> default) 42 6728fb62-c2b9-46cc-91c1-f02208412434 58 89 0.12361111111111112 68565 19.045833333333334 267797 33 20180924 2018-09-14T16:00:00.0+03:00 2018-09-17T00:00:00.0+03:00 shutdow

In [96]:
# summary stats for client 7728 for week
display(dup_c1['uri_count', 'active_ticks', 'active_tick_hrs', 'subsession_length', 'subsession_hours', 'profile_subsession_counter', 'submission_date_s3', 'country'].describe())

summary uri_count active_ticks active_tick_hrs subsession_length subsession_hours profile_subsession_counter submission_date_s3 country count 54 54 54 54 54 54 54 54 mean 53.03703703703704 86.75925925925925 0.12049897119341563 23540.296296296296 6.538971193415637 35.0 2.0180924722222224E7 null stddev 10.461002085847792 31.842735722749623 0.044226021837152255 19577.038650563223 5.438066291823119 1.00938987736568 0.9400254246518539 null min 14 22 0.030555555555555555 137 0.03805555555555556 33 20180924 RU max 58 114 0.15833333333333333 68565 19.045833333333334 37 20180927 RU

In [97]:
# Show duplicate counts by profile_subsession_counter for client 7728 over the week
dup_c1_count = dup_c1.groupBy("submission_date_s3", "profile_subsession_counter") \
  .agg(F.count(F.lit(1)).alias("num_records"), F.min("os")) \
  . sort("submission_date_s3", "profile_subsession_counter")
display(dup_c1_count)

submission_date_s3 profile_subsession_counter num_records min(os) 20180924 33 7 Windows_NT 20180924 34 4 Windows_NT 20180924 35 16 Windows_NT 20180925 35 9 Windows_NT 20180925 36 12 Windows_NT 20180927 35 2 Windows_NT 20180927 36 2 Windows_NT 20180927 37 2 Windows_NT

In [98]:
#Look at profile counter 35 for client 7728 for 9/24
dup_c1_3524 = dup_c1.where("profile_subsession_counter = 35 and submission_date_s3 = '20180924'").sort("submission_date_s3", "profile_subsession_counter")
display(dup_c1_3524['uri_count', 'active_ticks', 'active_tick_hrs', 'subsession_length', 'subsession_hours', 'profile_subsession_counter', 'submission_date_s3', 'client_submission_date', 'country'].describe())

summary uri_count active_ticks active_tick_hrs subsession_length subsession_hours profile_subsession_counter submission_date_s3 client_submission_date country count 16 16 16 16 16 16 16 16 16 mean 56.0 114.0 0.15833333333333327 24545.0 6.818055555555556 35.0 2.0180924E7 null null stddev 0.0 0.0 0.0 0.0 0.0 0.0 0.0 null null min 56 114 0.15833333333333333 24545 6.8180555555555555 35 20180924 Mon, 24 Sep 2018 06:16:06 GMT RU max 56 114 0.15833333333333333 24545 6.8180555555555555 35 20180924 Mon, 24 Sep 2018 08:16:13 GMT RU

There are lots of records in one week for client c62d.  Any patterns?  
Mostly 0 uri and active ticks.  Tab count and client submission date are often null.

In [100]:
# One week of pings for client c62d
diff_psc_c1 = ms_1week_raw.where("client_id like '%f2a01cedc62d'").sort("submission_date_s3", "profile_subsession_counter")
display(diff_psc_c1.select(ms_1week_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 0 0 0.0 406 0.11277777777777778 408 1 20180923 2018-09-22T00:00:00.0+08:00 2018-09-22T00:00:00.0+08:00 shutdown 0 null null null 16897 17796 null release Windows_NT 6.1 null 2018 2018-09-22T12:47:39.581Z null 20180923 20150917150946 null release true true null 480 Mozilla true baidu null null null null null null null null null null CN Zhengzhou HA zh-CN null null null 3b31cf18-4639-414a-b787-940fc9d630f4 6ff9fbbd-a967-4896-924c-3a2db6a0af4a null null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, 默认, false, false, 41.0, 4, null, false, false, 16897, 16897, null, null, null, null) null null 42 9f32d3e1-f8c4-42bb-ac93-041dee3cbbae 0 0 0.0 3565 0.9902777777777778 3565 3 20180923 2018-09-22T00:00:00.0+08:00 2018-09-22T00:00:00.0+08:00 shutdown 0 null null null 16897 null null release Windows_NT 6.1 null 2018 2018-09-22T12:03:28.048Z null 20180923 20150917150946 null release false false null 480 Mozilla false baidu null 8 22 null null null null null null null CN Shenyang LN zh-CN null null null cc915440-eba9-4c82-91fc-e646225e0df0 ff201bc2-1242-44f3-8f0c-0de6e8c13673 null null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, 默认, false, false, 41.0, 4, null, false, false, 16897, 16897, null, null, null, null) null null 42 17c4ec47-b386-466a-af38-03fc9410fae7 0 0 0.0 146 0.04055555555555555 147 3 20180923 2016-04-06T00:00:00.0+08:00 2016-04-06T00:00:00.0+08:00 shutdown 0 null null null 16897 null null release Windows_NT 6.1 null 2016 2016-04-06T09:37:48.447Z null 20180923 20150917150946 null release false false null 480 Mozilla true baidu null null null null null null null null null null CN Nanjing JS zh-CN null null null 695d7687-a786-4f26-a379-afe598715388 65488431-d41b-4c3b-ad36-91cb191704f8 null null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, 默认, false, false, 41.0, 4, null, false, false, 16897, 16897, null, null, null, null) null null 42 6c725a1e-2c23-49c0-b45d-3396d0b295f0 0 0 0.0 146 0.04055555555555555 147 3 20180923 2016-04-06T00:00:00.0+08:00 2016-04-06T00:00:00.0+08:00 shutdown 0 null null null 16897 null null release Windows_NT 6.1 null 2016 2016-04-06T09:37:48.447Z null 20180923 20150917150946 null release false false null 480 Mozilla true baidu null null null null null null null null null null CN Nanjing JS zh-CN null null null 695d7687-a786-4f26-a379-afe598715388 65488431-d41b-4c3b-ad36-91cb191704f8 null null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, 默认, false, false, 41.0, 4, null, false, false, 16897, 16897, null, null, null, null) null null 42 6c725a1e-2c23-49c0-b45d-3396d0b295f0 0 0 0.0 20 0.005555555555555556 21 4 20180923 2016-04-06T00:00:00.0+08:00 2016-04-06T00:00:00.0+08:00 shutdown 0 null null null 16897 null null release Windows_NT 6.1 null 2016 2016-04-06T09:38:09.568Z null 20180923 20150917150946 null release false false null 480 Mozilla true baidu null null null null null null null null null null CN Nanjing JS zh-CN null null null ce20d941-

In [101]:
# Summary stats for 1 week of pings for client c62d
display(diff_psc_c1['uri_count', 'active_ticks', 'active_tick_hrs', 'subsession_length', 'subsession_hours', 'profile_subsession_counter', 'submission_date_s3', 'tab_count', 'client_submission_date', 'country'].describe())

summary uri_count active_ticks active_tick_hrs subsession_length subsession_hours profile_subsession_counter submission_date_s3 tab_count client_submission_date country count 37964 37964 37964 37964 37964 37964 37964 3045 3180 37964 mean 6.4097302707828465 43.11584659150775 0.05988312026598293 23342.234880413023 6.4839541334480595 398.1462438099252 2.0180926617427036E7 9.826600985221674 null null stddev 43.611186174064834 287.1599726519931 0.3988332953499903 35675.50003473989 9.909861120761077 530.4441685399153 1.731948226514994 13.44732808020908 null null min 0 0 0.0 0 0.0 1 20180923 1 Fri, 28 Sep 2018 00:01:44 GMT CN max 1741 6761 9.390277777777778 2165662 601.5727777777778 6696 20180929 215 Wed, 26 Sep 2018 23:26:13 GMT US

In [102]:
# All the countries for client c62d
diff_psc_c1.select("country").distinct().show()

+-------+
country|
+-------+
 CN|
 RU|
 HK|
 DE|
 KR|
 US|
 MY|
 SG|
 TH|
 JP|
+-------+

One profile subsession counter for client c62d

In [104]:
# Look at one profile_subsession_counter
diff_psc_c12 = diff_psc_c1.where("profile_subsession_counter = 12").sort("submission_date_s3", "profile_subsession_counter")
display(diff_psc_c12.select(ms_1week_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 0 0 0.0 1814 0.5038888888888889 1817 12 20180923 2018-09-21T00:00:00.0+08:00 2018-09-21T00:00:00.0+08:00 shutdown 0 null null null 16897 null null release Windows_NT 6.1 null 2018 2018-09-21T01:29:21.072Z null 20180923 20150917150946 null release false false null 480 Mozilla true baidu null null null null null null null null null null CN ?? JS zh-CN null null null 46ba99e7-da8d-4497-80f3-48f264c35049 732140d3-59ed-445b-9cfc-38975571c6bc null null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, 默认, false, false, 41.0, 4, null, false, false, 16897, 16897, null, null, null, null) null null 42 c2522331-4727-4159-a3df-75c17b21da04 0 0 0.0 38 0.010555555555555556 40 12 20180923 2018-09-23T00:00:00.0+08:00 2018-09-23T00:00:00.0+08:00 shutdown 0 null null null 16897 null null release Windows_NT 6.1 null 2018 2018-09-23T00:59:19.214Z null 20180923 20150917150946 null release false false null 480 Mozilla true baidu null null null null null null null null null null CN ?? JS zh-CN null null null 1af75400-97d0-4aaa-bcb6-9716e23bd1d8 81377176-5062-4565-a9d5-d99b8a946069 null null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, 默认, false, false, 41.0, 4, null, false, false, 16897, 16897, null, null, null, null) null null 42 c3ab3c97-0408-4cf8-81af-c8ebbbfe5b5e 0 0 0.0 33055 9.181944444444444 33055 12 20180923 2018-09-22T00:00:00.0+08:00 2018-09-22T00:00:00.0+08:00 aborted-session 0 null null null 16897 null null release Windows_NT 6.1 null 2018 2018-09-22T10:07:58.073Z null 20180923 20150917150946 null release false false null 480 Mozilla false baidu null 14 210 null null null null null null null CN Foshan GD zh-CN null null null 4343a616-9138-4961-ba42-0777348e32ca 971b3af7-c75c-4cad-a24e-617f74317aef null null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, 默认, false, false, 41.0, 4, null, false, false, 16897, 16897, null, null, null, null) null null 42 2d3dfaae-1eeb-48fe-b714-9123572b401e 0 0 0.0 88180 24.494444444444444 229999 12 20180923 2018-09-20T00:00:00.0+08:00 2018-09-22T00:00:00.0+08:00 daily 0 null null null 16897 null null release Windows_NT 6.1 null 2016 2018-09-23T01:11:40.247Z null 20180923 20150917150946 null release false false null 480 Mozilla false baidu null 8 201 null null null null null null null CN ?? JS zh-CN null null null 0e659775-4e22-4f63-8a91-b2534677bd6e ee92e90b-7a70-4bb3-b620-f58daab09089 null null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, 默认, false, false, 41.0, 4, null, false, false, 16897, 16897, null, null, null, null) null null 42 c2d91179-df11-42cb-9c88-7bd0153f8f61 0 0 0.0 32159 8.933055555555555 32159 12 20180923 2018-09-22T00:00:00.0+08:00 2018-09-22T00:00:00.0+08:00 shutdown 2 null null null 16897 null null release Windows_NT 6.1 null 2018 2018-09-22T10:02:09.922Z null 20180923 20150917150946 null release false false null 480 Mozilla true baidu null 8 133 null null null null null null null CN Tianjin TJ zh-CN null null null 9b5639a2-8fb0-4

In [105]:
# Summary stats for profile counter 12 for client c62d
display(diff_psc_c12['uri_count', 'active_ticks', 'active_tick_hrs', 'subsession_length', 'subsession_hours', 'profile_subsession_counter', 'submission_date_s3', 'country'].describe())

summary uri_count active_ticks active_tick_hrs subsession_length subsession_hours profile_subsession_counter submission_date_s3 country count 151 151 151 151 151 151 151 151 mean 0.006622516556291391 0.2185430463576159 3.035320088300221E-4 23268.039735099337 6.463344370860926 12.0 2.0180926509933773E7 null stddev 0.08137884587711594 2.6855019139448264 0.0037298637693678137 47521.49683260981 13.200415786836055 0.0 1.6965358816678506 null min 0 0 0.0 3 8.333333333333334E-4 12 20180923 CN max 1 33 0.04583333333333333 409930 113.86944444444444 12 20180929 CN

Look at pings for client c62d where the active ticks > 10

In [107]:
# Active ticks > 10
diff_psc_high = diff_psc_c1.where("active_ticks > 10").sort("submission_date_s3", "profile_subsession_counter")
display(diff_psc_high.select(ms_1week_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 76 519 0.7208333333333333 17486 4.857222222222222 17490 16 20180923 2018-09-23T09:00:00.0+08:00 2018-09-23T09:00:00.0+08:00 environment-change 8 7 2 5 16897 null 20150917150946 release Windows_NT 6.1 7601 2018 2018-09-23T06:16:47.178Z null 20180923 20180830143136 62.0 release false false null 480 Mozilla false baidu Sun, 23 Sep 2018 06:16:47 GMT null null null 29 1 null null false null CN Wuhan HB zh-CN null null null 395fd600-6959-42d5-b9cd-9abd6281e26b 8d88afad-e6c6-4ddb-a1d7-4841c5753846 null null null null List(default-theme@mozilla.org, false, 默认, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null null 42 98fe97fc-530f-41f7-9645-b53e66bc2e7b 56 838 1.163888888888889 30156 8.376666666666667 30156 25 20180923 2018-09-23T09:00:00.0+08:00 2018-09-23T09:00:00.0+08:00 shutdown 11 14 1 3 16897 null null release Windows_NT 6.1 7601 2016 2018-09-23T09:53:49.132Z null 20180923 20171002220106 56.0.1 release false false null 480 Mozilla true baidu Sun, 23 Sep 2018 09:53:50 GMT 16 238 null 33 null null Map(light -> 1) false null CN ?? HN zh-CN null null null 2b3fbd79-054d-4501-936f-a0d651fe5ca4 eed50229-23ca-40c1-a092-a4c1191bad06 null null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, 默认, false, false, 56.0.1, 4, null, false, false, 17342, 17443, null, null, null, null) null Map(clicktoplay-rollout -> test, e10sCohort -> disqualified-test) 42 4eaa9edc-1f08-47e5-aa33-17f49398045f 117 1431 1.9875 31460 8.738888888888889 31461 28 20180923 2018-09-23T09:00:00.0+08:00 2018-09-23T09:00:00.0+08:00 shutdown 10 14 2 5 16897 null null release Windows_NT 6.1 7601 2016 2018-09-23T10:04:07.654Z null 20180923 20180830143136 62.0 release false false null 480 Mozilla true baidu Sun, 23 Sep 2018 10:04:08 GMT 13 1272 null 81 1 null null false null CN ?? GD zh-CN null null null 9cae2481-39cc-451e-88ea-c748e238e5d2 2e834b60-3689-4b81-8f57-147f3c23853a null null null null List(default-theme@mozilla.org, false, 默认, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null null 42 07f23eda-67dc-4435-b642-a8c67c245f7a 91 1024 1.4222222222222223 22322 6.200555555555556 27195 44 20180923 2018-09-21T14:00:00.0+08:00 2018-09-21T16:00:00.0+08:00 shutdown 9 20 2 6 16897 17776 null release Windows_NT 6.1 7601 2017 2018-09-21T14:26:34.516Z null 20180923 20180830143136 62.0 release true true null 480 Mozilla true baidu Sun, 23 Sep 2018 11:46:02 GMT 15 1133 null 50 null null null null null CN Shenzhen GD zh-CN null null null 8eefeeaf-58ba-49b1-9c3e-f504b81d8aac 6a0c2300-5418-4cd9-a6cc-26dd575d9eba null null null null List(default-theme@mozilla.org, false, 默认, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null null 42 4fd73217-2e2e-40c9-be85-1eb655ebb599 14 95 0.13194444444444445 6076 1.6877777777777778 6078 45 20180923 2018-09-23T19:00:00.0+08:00 2018-09-23T19:00:00.0+08:00 shutdown 9 4 1 4 16897 17776 null release Windows_NT 6.1 7601 2017 2018-09-23T13:26:17.842Z null 20180923 2018083014313

In [108]:
# Summary stats for client c62d with active ticks > 10
display(diff_psc_high.select(ms_1week_raw_cols).describe())

summary uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel active_experiment_branch timezone_offset vendor default_search_engine client_submission_date places_bookmarks_count places_pages_count tab_event_count window_event_count errors_collected_count media_page_count country city geo_subdivision1 locale session_id subsession_id sync_count_desktop sync_count_mobile sample_id document_id count 2279 2279 2279 2279 2279 2279 2279 2279 2279 2279 2279 2279 2279 2279 2258 2279 1144 296 2279 2279 2279 2279 2279 2279 543 2279 2279 2279 2279 0 2279 2279 2279 2267 1190 1190 2176 455 0 0 2279 2279 2251 2279 2279 2279 38 38 2279 2279 mean 99.8354541465555 717.4655550680122 0.9964799375944621 26268.310662571304 7.29675296182536 94696.9319877139 546.8442299254059 2.0180926687582273E7 null null null 10.917068889863975 11.057920140412461 1.3852566915313733 4.629760850310009 16897.0 17524.712412587414 2.0168020962127348E13 null null 6.100000000000014 7601.0 2016.861342694164 null null 2.0180926687582273E7 2.0179913717693297E13 60.97789115646258 null null 480.0 null null null 52.15714285714286 9907.705042016807 47.02711397058823 3.8461538461538463 null null null null 1.0 null null null 1.3157894736842106 0.0 42.0 null stddev 142.46164139595453 943.5084398413369 1.3104283886685224 35777.3306740429 9.938147409456366 245907.7244005454 623.4483480719299 1.6805396742339394 null null null 2.7357521416586903 13.445241504484061 0.880912764123809 4.681077400743308 0.0 213.81320778846995 1.4265691426435263E10 null null 0.0 0.0 0.741407996383173 null null 1.6805396742339394 2.7029795762474885E9 1.9711343619781632 null null 0.0 null null null 75.42744810684377 15497.19212179332 70.61441160672202 8.779134098926843 null null null null 0.0 null null null 0.4710691208760757 0.0 0.0 null min 0 11 0.015277777777777777 51 0.014166666666666666 52 6 20180923 2018-08-30T16:00:00.0+08:00 2018-09-11T11:00:00.0+08:00 aborted-session 8 1 1 1 16897 16963 20150917150946 beta Windows_NT 6.1 7601 2016 2018-09-11T11:05:45.690Z MozillaOnline 20180923 20170926190823 56.0 beta null 480 Mozilla baidu Fri, 28 Sep 2018 00:01:44 GMT 8 34 1 1 null null CN ?? 01 en-US 000fc22d-a15e-47f9-ae96-5938d3c62d93 0033c69f-b02d-4dc1-8fcc-974411ef2964 1 0 42 00024297-b436-4d7b-be4b-59b2d2f06c73 max 1741 6761 9.390277777777778 430770 119.65833333333333 2219344 5882 20180929 2018-09-29T22:00:00.0+08:00 2018-09-29T22:00:00.0+08:00 shutdown 26 215 10 69 16897 17801 20180920131237 release Windows_NT 6.1 7601 2018 2018-09-29T16:04:15.335Z MozillaOnline 20180929 20180920175354 62.0.2 release null 480 Mozilla google-nocodes Wed, 26 Sep 2018 16:59:59 GMT 766 134975 784 122 null null SG Zhongshan ZJ zh-CN ffde3cc0-56ec-489d-b4c2-0455dcfc4271 ffbaaa75-839e-4a9b-bd24-f47d0d18b80d 2 0 42 ffdb1d2a-273a-4c41-8547-5e2b96c6d963

Clearly different users with same client_id  
Profile subsession counters don't increment

In [110]:
# week of pings for client e43c
diff_psc_c2 = ms_1week_raw.where("client_id like '%5d25a3e4e43c'").sort("submission_date_s3", "profile_subsession_counter")
display(diff_psc_c2.select(ms_1week_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 0 0 0.0 28546 7.929444444444444 83351 884 20180923 2018-09-22T08:00:00.0+02:00 2018-09-23T00:00:00.0+02:00 shutdown 11 1 1 null 16267 null null release Windows_NT 6.3 9600 2014 2018-09-23T05:55:46.019Z null 20180923 20180830143136 62.0 release true true null 120 Mozilla false google Sun, 23 Sep 2018 05:55:46 GMT null null null null null null null null null DE ?? BY de List(Avira Antivirus) List(Avira Antivirus) List(Windows-Firewall) 7fcbc21a-cfef-4d76-8073-fc9cc3c8b792 3bc117cc-f128-4a83-8f96-acee05baff24 null null null null List(default-theme@mozilla.org, false, Standard, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null null 42 4448d137-d7a6-45f0-b207-06d62785ed63 5 7 0.009722222222222222 40 0.011111111111111112 40 1495 20180923 2018-09-23T14:00:00.0+02:00 2018-09-23T14:00:00.0+02:00 shutdown 10 3 2 3 16267 null null release Windows_NT 6.3 9600 2014 2018-09-23T12:33:31.019Z null 20180923 20180830143136 62.0 release true true null 120 Mozilla false google Sun, 23 Sep 2018 12:33:31 GMT null null null 2 1 null null false null DE ?? NI de null null List(Windows-Firewall) 0f6178af-9d9f-485b-b401-8d0ef4a9d8a6 4e931c20-2e07-4ae2-b4d0-23fd6677909b null null null null List(default-theme@mozilla.org, false, Standard, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null null 42 35599e94-996f-45b9-89c8-5b2e77e98837 0 3 0.004166666666666667 30683 8.523055555555555 71585 1791 20180923 2018-09-22T12:00:00.0+02:00 2018-09-23T00:00:00.0+02:00 shutdown 11 1 1 null 16267 null null release Windows_NT 6.3 9600 2014 2018-09-23T06:31:23.316Z null 20180923 20180830143136 62.0 release true true null 120 Mozilla false google Sun, 23 Sep 2018 06:31:23 GMT null null null null null null null null null DE Augsburg BY de List(Avira Antivirus) List(Avira Antivirus) List(Windows-Firewall) 43b8b04e-336b-489a-9516-12c2260c532d ab7d9a0c-cdaf-4551-8e22-0f79c777648e null null null null List(default-theme@mozilla.org, false, Standard, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null null 42 8a8c834f-d6e0-4848-998f-645953d5185c 1 2 0.002777777777777778 7 0.0019444444444444444 9 2259 20180923 2018-09-23T08:00:00.0+02:00 2018-09-23T08:00:00.0+02:00 shutdown 11 1 1 1 16267 null null release Windows_NT 6.3 9600 2014 2018-09-23T06:34:47.931Z null 20180923 20180830143136 62.0 release true true null 120 Mozilla false google Sun, 23 Sep 2018 06:34:48 GMT null null null null null null null false null DE Nordhorn NI de List(Avira Antivirus) List(Avira Antivirus) List(Windows-Firewall) b9c0f958-3f71-4dca-9375-18d6eb538b84 0f9cc0e6-0375-42b2-83bc-63da863690d5 null null null null List(default-theme@mozilla.org, false, Standard, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null null 42 fbda0f8b-7a60-4b7c-8460-25e3ae0f6595 13 44 0.06111111111111111 473 0.1313888888888889 474 45 20180924 2018-09-24T09:00:00.0+02:00 2018-09-24T09:00:00.0+02:00 shutdown 11 2 1 2 16267 null null release Win

In [111]:
# Summary stats for 1 week of client e43c
display(diff_psc_c2.select(ms_1week_raw_cols).describe())

summary uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel active_experiment_branch timezone_offset vendor default_search_engine client_submission_date places_bookmarks_count places_pages_count tab_event_count window_event_count errors_collected_count media_page_count country city geo_subdivision1 locale session_id subsession_id sync_count_desktop sync_count_mobile sample_id document_id count 2575 2575 2575 2575 2575 2575 2575 2575 2575 2575 2575 2575 2546 2546 2293 2575 140 221 2575 2575 2575 2548 2575 2575 0 2575 2575 2549 2575 0 2575 2575 2575 2549 553 553 707 154 0 0 2575 2575 2573 2575 2575 2575 0 0 2575 2575 mean 10.910291262135923 34.83300970873786 0.0483791801510248 3255.4796116504854 0.9042998921251348 3588.184854368932 2748.9549514563105 2.018092604699029E7 null null null 10.440388349514564 1.5926944226237234 1.0691280439905735 2.6040122110771913 16267.0 17154.05 2.018069238470829E13 null null 6.370407766990282 9744.884615384615 2014.1308737864078 null null 2.018092604699029E7 2.0180575898431688E13 61.952302631578945 null null 120.0 null null null 15.994575045207956 6583.359855334539 2.6605374823196604 1.7987012987012987 null null null null null null null null null null 42.0 null stddev 20.812126990495543 64.17800188735093 0.08913611373243184 7414.552935711785 2.059598037697717 9144.165580094266 2285.356180405739 1.5554144069190352 null null null 1.172496193543304 1.5634107236643493 0.2816129966203352 2.0286390919273574 0.0 468.0593844909758 1.4862560213426304E9 null null 0.5056191907576458 1034.8862092368786 0.6721498097424198 null null 1.5554144069190352 3.0294337627202234E9 0.4210616070859022 null null 7.141223187966347E-16 null null null 16.689892352811455 10724.374411789951 3.104535883748129 1.6345128599308572 null null null null null null null null null null 0.0 null min 0 0 0.0 1 2.777777777777778E-4 1 22 20180923 2018-09-18T00:00:00.0+02:00 2018-09-18T00:00:00.0+02:00 aborted-session 0 1 1 1 16267 16566 20161031133903 release Windows_NT 10.0 9600 2014 2018-09-18T15:43:20.419Z null 20180923 20151029151421 47.0.2 release null 120 Mozilla bing Fri, 28 Sep 2018 05:53:35 GMT 2 4 1 1 null null DE ?? BE de 0000010a-7e7d-4b40-b725-ea34f3fdf9b7 0006e024-90f6-4764-9bd5-065a7b88f081 null null 42 00012870-db44-4a19-9365-95edaa9aab63 max 379 894 1.2416666666666667 73570 20.43611111111111 120119 8432 20180929 2018-09-29T23:00:00.0+02:00 2018-09-29T23:00:00.0+02:00 shutdown 13 23 4 30 16267 17784 20180830143136 release Windows_NT 6.3 17134 2018 2018-09-29T22:00:00.011Z null 20180929 20180920131237 62.0.2 release null 120 Mozilla other-Bing Search Engine Wed, 26 Sep 2018 22:47:36 GMT 143 77314 29 12 null null DE Wurzburg ST de ffe6a013-58da-4d2f-a369-3da0753caeab fffedf23-7158-46ed-8ed5-cffbc47ff477 null null 42 fff10b98-827b-4ebf-8536-e68ac5c9a6c3

In [112]:
# All the cities in Germany for this client e43c
display(diff_psc_c2.select("country", "city").distinct())

country city DE Wunstorf DE Gütersloh DE Dortmund DE Aurich DE Hamburg DE Oldenburg DE ?? DE Papenburg DE Hemmingen DE Nordhorn DE Porta Westfalica DE Lippstadt DE Freiburg DE Wolfenbüttel DE Coesfeld DE Hagen DE Alfter DE Edewecht DE Vechta DE Lübeck DE Hemer DE Duisburg DE Paderborn DE Ludwigsburg DE Leer DE Ganderkesee DE Ronnenberg DE Eltville DE Konigsbrunn DE Halle DE Neumünster DE Munster DE Berlin DE Osnabrück DE Geseke DE Schweinfurt DE Weener DE Salzgitter DE Schwalmtal DE Erlangen DE Cologne DE Stuttgart DE Schortens DE Nuremberg DE Kevelaer DE Recklinghausen DE Soltau DE Gladbeck DE Georgsmarienhuette DE Merseburg DE Frankfurt am Main DE Augsburg DE Leutkirch im Allgau DE Stade DE Stuhr DE Voerde DE Bochum DE Münster DE Emden DE Bramsche DE Marl DE Varel DE Landshut DE Wurzburg DE Pfaffenhofen an der Ilm DE Bremen DE Fürth DE Garbsen DE Lüneburg DE Braunschweig DE Offenburg DE Neustadt am Ruebenberge DE Wolfsburg DE Flensburg DE Waiblingen DE Langenfeld DE Bad Oldesloe DE Cloppenburg DE Rheine DE Pinneberg

####High URI count, 0 active ticks

In [114]:
# Look at client with high uri count and 0 active ticks
ms_1week_check = ms_1week_raw.where("client_id like '%c0636c4d3afd'")
display(ms_1week_check.select(ms_1week_raw_cols))
# This pattern holds for multiple days, reasonable subsession_length, reasonable domains_count

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 2171 0 0.0 21132 5.87 21133 663 20180924 2018-09-21T00:00:00.0+02:00 2018-09-21T00:00:00.0+02:00 aborted-session 4 10 3 9 16652 null null esr Windows_NT 6.1 null 2012 2018-09-21T15:50:54.693Z null 20180924 20180118122319 52.6.0 esr false false null 120 Mozilla false google Mon, 24 Sep 2018 07:17:56 GMT 32 253577 null 13 2 null null null null DE Hamburg HH de null null null 28bf2b46-d56f-4414-b88f-92ca9adfc1c5 fd012160-66a4-4171-a20a-cc46ac8e3861 false null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Standard, false, false, 52.6.0, 4, null, false, false, 16381, 17549, null, null, null, null) null null 42 5fb3f17f-3934-4c08-b576-ee8397d0d06b 1406 0 0.0 21055 5.848611111111111 21057 666 20180925 2018-09-24T00:00:00.0+02:00 2018-09-24T00:00:00.0+02:00 shutdown 4 10 3 8 16652 null 20160601155443 esr Windows_NT 6.1 null 2012 2018-09-24T13:07:49.140Z null 20180925 20180118122319 52.6.0 esr false false null 120 Mozilla false google Tue, 25 Sep 2018 10:00:23 GMT 32 253514 null 16 2 null null null null DE Hamburg HH de null null null 65b2d9e0-b49d-4cec-8fa2-be09b7976672 2340c112-058b-48b4-874d-1a73bf523283 false null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Standard, false, false, 52.6.0, 4, null, false, false, 16381, 17549, null, null, null, null) null null 42 f9008635-160d-4ef0-8f5d-eefdb76d506e 3115 0 0.0 22497 6.2491666666666665 22498 667 20180926 2018-09-25T00:00:00.0+02:00 2018-09-25T00:00:00.0+02:00 shutdown 4 13 4 16 16652 null null esr Windows_NT 6.1 null 2012 2018-09-25T16:14:19.566Z null 20180926 20180118122319 52.6.0 esr false false null 120 Mozilla false google Wed, 26 Sep 2018 12:57:20 GMT 32 253401 null 35 5 null null null null DE Hamburg HH de null null null 6a23fe73-e768-4df4-a5b0-89d656f0d89f b7c05b5a-830b-48cf-af06-561218c2db11 false null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Standard, false, false, 52.6.0, 4, null, false, false, 16381, 17549, null, null, null, null) null null 42 92e2d8a7-4c47-4731-8660-9a263c8d9a73 3159 0 0.0 18265 5.073611111111111 18265 668 20180927 2018-09-26T00:00:00.0+02:00 2018-09-26T00:00:00.0+02:00 shutdown 4 11 3 10 16652 null null esr Windows_NT 6.1 null 2012 2018-09-26T18:00:43.988Z null 20180927 20180118122319 52.6.0 esr false false null 120 Mozilla false google Thu, 27 Sep 2018 08:06:57 GMT 32 253850 null 22 5 null null null null DE Hamburg HH de null null null da5c2db6-517b-46ac-a816-91c6269f551b 9d43d4ce-266e-4963-9b2e-f6448da45ca7 false null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Standard, false, false, 52.6.0, 4, null, false, false, 16381, 17549, null, null, null, null) null null 42 b12394b3-ade7-4b1e-bb2a-5f66a5d6e825 2350 0 0.0 25049 6.958055555555555 25050 669 20180929 2018-09-27T00:00:00.0+02:00 2018-09-27T00:00:00.0+02:00 shutdown 4 13 3 10 16652 null null esr Windows_NT 6.1 null 2012 2018-09-27T15:03:26.076Z null 20180929 20180118122319 52.6.0 esr false false null 120 Mozilla false google Sat, 

In [115]:
# Look at client ^ for 4 weeks
ms_4week_check = ms_4week_raw.where("client_id like '%c0636c4d3afd'")
display(ms_4week_check.select(ms_1week_raw_cols))
# Same pattern over 4 weeks, profile_subsession_counter in order

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 2171 0 0.0 21132 5.87 21133 663 20180924 2018-09-21T00:00:00.0+02:00 2018-09-21T00:00:00.0+02:00 aborted-session 4 10 3 9 16652 null null esr Windows_NT 6.1 null 2012 2018-09-21T15:50:54.693Z null 20180924 20180118122319 52.6.0 esr false false null 120 Mozilla false google Mon, 24 Sep 2018 07:17:56 GMT 32 253577 null 13 2 null null null null DE Hamburg HH de null null null 28bf2b46-d56f-4414-b88f-92ca9adfc1c5 fd012160-66a4-4171-a20a-cc46ac8e3861 false null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Standard, false, false, 52.6.0, 4, null, false, false, 16381, 17549, null, null, null, null) null null 42 5fb3f17f-3934-4c08-b576-ee8397d0d06b 1406 0 0.0 21055 5.848611111111111 21057 666 20180925 2018-09-24T00:00:00.0+02:00 2018-09-24T00:00:00.0+02:00 shutdown 4 10 3 8 16652 null 20160601155443 esr Windows_NT 6.1 null 2012 2018-09-24T13:07:49.140Z null 20180925 20180118122319 52.6.0 esr false false null 120 Mozilla false google Tue, 25 Sep 2018 10:00:23 GMT 32 253514 null 16 2 null null null null DE Hamburg HH de null null null 65b2d9e0-b49d-4cec-8fa2-be09b7976672 2340c112-058b-48b4-874d-1a73bf523283 false null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Standard, false, false, 52.6.0, 4, null, false, false, 16381, 17549, null, null, null, null) null null 42 f9008635-160d-4ef0-8f5d-eefdb76d506e 3115 0 0.0 22497 6.2491666666666665 22498 667 20180926 2018-09-25T00:00:00.0+02:00 2018-09-25T00:00:00.0+02:00 shutdown 4 13 4 16 16652 null null esr Windows_NT 6.1 null 2012 2018-09-25T16:14:19.566Z null 20180926 20180118122319 52.6.0 esr false false null 120 Mozilla false google Wed, 26 Sep 2018 12:57:20 GMT 32 253401 null 35 5 null null null null DE Hamburg HH de null null null 6a23fe73-e768-4df4-a5b0-89d656f0d89f b7c05b5a-830b-48cf-af06-561218c2db11 false null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Standard, false, false, 52.6.0, 4, null, false, false, 16381, 17549, null, null, null, null) null null 42 92e2d8a7-4c47-4731-8660-9a263c8d9a73 3159 0 0.0 18265 5.073611111111111 18265 668 20180927 2018-09-26T00:00:00.0+02:00 2018-09-26T00:00:00.0+02:00 shutdown 4 11 3 10 16652 null null esr Windows_NT 6.1 null 2012 2018-09-26T18:00:43.988Z null 20180927 20180118122319 52.6.0 esr false false null 120 Mozilla false google Thu, 27 Sep 2018 08:06:57 GMT 32 253850 null 22 5 null null null null DE Hamburg HH de null null null da5c2db6-517b-46ac-a816-91c6269f551b 9d43d4ce-266e-4963-9b2e-f6448da45ca7 false null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Standard, false, false, 52.6.0, 4, null, false, false, 16381, 17549, null, null, null, null) null null 42 b12394b3-ade7-4b1e-bb2a-5f66a5d6e825 2350 0 0.0 25049 6.958055555555555 25050 669 20180929 2018-09-27T00:00:00.0+02:00 2018-09-27T00:00:00.0+02:00 shutdown 4 13 3 10 16652 null null esr Windows_NT 6.1 null 2012 2018-09-27T15:03:26.076Z null 20180929 20180118122319 52.6.0 esr false false null 120 Mozilla false google Sat, 

In [116]:
# How many clients in 1 week have this pattern?
ms_1week_highuri_0at = ms_1week_raw.where("uri_count > 1000 and active_ticks = 0").sort("client_id")
display(ms_1week_highuri_0at.select(ms_1week_raw_cols))

uri_count active_ticks active_tick_hrs subsession_length subsession_hours session_length profile_subsession_counter submission_date_s3 session_start_date subsession_start_date reason active_addons_count tab_count window_count domains_count profile_creation_date profile_reset_date previous_build_id normalized_channel os normalized_os_version windows_build_number install_year creation_date distribution_id submission_date app_build_id app_display_version update_channel update_enabled update_auto_download active_experiment_branch timezone_offset vendor is_default_browser default_search_engine client_submission_date places_bookmarks_count places_pages_count telem_event_counts tab_event_count window_event_count errors_collected_count current_theme formautofill_availability media_page_count country city geo_subdivision1 locale antivirus antispyware firewall session_id subsession_id sync_configured sync_count_desktop sync_count_mobile disabled_addons_ids active_theme user_prefs experiments sample_id document_id 6322 0 0.0 84423 23.450833333333332 94778 1064 20180927 2018-09-26T07:00:00.0-05:00 2018-09-26T10:00:00.0-05:00 daily 9 1 1 1 17017 null null release Windows_NT 6.1 7601 2011 2018-09-27T14:58:39.184Z null 20180927 20180807170231 61.0.2 release true true null -300 Mozilla false google-2018 Thu, 27 Sep 2018 15:00:40 GMT 12 5723 null null null null null null null US Pearl MS en-US null null null a980e394-5ff2-4aef-8db4-35352ccc180d 0f166277-5ce8-4020-bde4-0bb7dbcb76c6 null null null null List(default-theme@mozilla.org, false, Default, false, false, , 1, null, false, false, 0, 0, null, null, null, null) null Map(rollout-release-61-tls-fallback-1-3 -> active, searchCohort -> nov17-2, rollout-restart-manager-release-1481278 -> active) 42 ab2f6717-f6ad-41c4-9e63-a571480a0c88 1057 0 0.0 24717 6.865833333333334 24718 653 20180925 2018-09-24T00:00:00.0-04:00 2018-09-24T00:00:00.0-04:00 shutdown 8 10 3 21 17392 null null release Windows_NT 10.0 15063 2017 2018-09-24T18:15:32.681Z HCPSS 20180925 20170628075643 54.0.1 release false false null -240 Mozilla true other-Search Tue, 25 Sep 2018 11:18:50 GMT null null null 36 12 null null null null US Ellicott City MD en-US null null null 776be78a-bcb6-4926-9972-4935a5175a24 550c2a6b-a237-490f-9df4-32133424ddee false null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Default, false, false, 54.0.1, 4, null, false, false, 17345, 17345, null, null, null, null) null null 42 e4e2c217-4bde-4fd1-b74b-24d8acf0716a 1117 0 0.0 31634 8.787222222222223 31638 642 20180929 2018-09-28T00:00:00.0+02:00 2018-09-28T00:00:00.0+02:00 shutdown 4 1 1 null 15890 null null esr Windows_NT 5.1 null 2009 2018-09-28T16:56:28.468Z null 20180929 20180621064021 52.9.0 esr true true null 120 Mozilla true google Sat, 29 Sep 2018 07:36:15 GMT 34 17606 null null null null null null null FR ?? null fr null null null b241d1ed-9534-4093-a9d4-5c155948a959 5c94aa5d-46f5-4595-a3b6-49bb944c934f false null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Thème par défaut, false, false, 52.9.0, 4, null, false, false, 16763, 17709, null, null, null, null) null null 42 22f996b7-ac66-487a-b463-a81c0785f179 14401 0 0.0 86404 24.00111111111111 3183347 778 20180923 2018-08-16T00:00:00.0-07:00 2018-09-22T00:00:00.0-07:00 daily 5 23 3 1 16200 null null esr Darwin 16.7.0 null null 2018-09-23T07:00:00.026Z null 20180923 20180621064021 52.9.0 esr true false null -420 Mozilla false google Sun, 23 Sep 2018 07:51:16 GMT 21 10649 null null null null null null null US Valencia CA en-US null null null 33525474-5b49-0945-9093-fb78a342e928 22c13beb-c859-d14a-a396-a75f3bf90b0c null null null null List({972ce4c6-7e08-4474-a285-3208198ce6fd}, false, Default, false, false, 52.9.0, 4, null, false, false, 16182, 17708, null, null, null, null) null null 42 a6cea845-b581-7a4b-b0e1-2bca2786fb07 7558 0 0.0 86404 24.00111111111111 3269752 779 20180924 2018-08-16T00:00:00.0-07:00 2018-09-23T00:00:00.0-07:00 daily 5 23 3 1 16200 null null esr

In [117]:
# Lots of clients in 1 week with high uri and 0 active ticks
ms_1week_check.select("client_id").distinct().count()

Out[ 183 ]: 1

In [118]:
# Look at how many pings each client has in a week with high uri and 0 active ticks
ms_1week_highuri_0at_count = ms_1week_highuri_0at.groupBy('client_id').count()
display(ms_1week_highuri_0at_count.select(['count']))

count 6 1 1 15 1 1 2 1 2 1 1 1 1 2 5 2 1 1 1 1 2 1 7 1 7 3 1 2 2 3 2 3 1 1 1 1 1 1 2 1 1 38 1 2 1 1 6 1 1 1 1 2 2 1 1 1 7 1 1 1 1 7 6 9 7 1 3 1 2 3 1 1 1 1 2 1 1 1 4 1 1 2 2 1 1 1 1 1 4 1 1 1 1 1 1 3 5 4 1 3 4 1 1 1 3 1 2 1 2 2 3 1 1 1 11 2 5 2 1 1 1 1 1 1 1 3 4 3 1 1 6 1 7 1 4 1 1 1 1 7 2 1 1 1 1 1 1 2 1 3 7 6 2 1 1 2 1 1 1 2 1 1 2 1 1 1 1 6 1 1 2 1 1 4 1 1 1 1 1 1 3 1 1 1 1 1 1 1 1 2 1 2 1 1 1 1 7 3 1 6 2 1 1 3 1 2 2 1 1 2 1 4 4 1 2 1 2 6 2 1 1 4 3 1 2 1 1 1 7 1 2 1 1 2 4 1 5 1 3 7 6 2 1 1 1 1 5 1 5 3 2 2 1 15 1 1 8 1 1 4 1 7 1 2 1 1 3 2 3 1 3 1 6 1 2 1 1 1 3 1 1 1 3 1 1 6 1 1 7 1 1 2 1 1 1 2 1 1 6 1 2 1 5 6 1 2 2 2 1 2 2 1 2 1 4 1 1 1 1 1 1 5 1 1 4 7 3 1 1 1 2 1 5 1 4 7 1 1 1 1 1 1 1 4 1 3 1 1 1 6 1 2 2 1 6 3 3 6 2 1 4 1 7 1 1 1 4 1 2 1 1 2 4 2 1 8 1 10 1 4 1 1 2 1 3 3 11 1 2 6 8 3 5 1 1 5 7 1 1 4 1 1 3 1 1 1 1 3 3 1 8 1 1 3 7 1 1 2 1 4 1 1 7 1 1 1 8 1 1 1 1 6 1 1 1 1 3 5 1 1 1 1 2 1 1 1 2 5 1 1 1 1 1 2 1 1 1 6 2 1 8 1 1 1 2 1 4 3 2 1 1 1 1 5 1 2 7 5 1 1 1 6 1 1 1 2 1 2 1 1 1 1 1 2 4 3 1 1 1 1 1 4 1 1 1 1 4 1 2 1 1 3 2 4 1 1 2 2 3 6 4 1 1 2 1 3 5 1 3 6 2 1 1 2 1 1 1 1 1 4 1 4 1 1 2 1 4 1 1 1 1 1 5 1 2 2 2 4 3 1 1 2 1 2 1 1 1 1 7 1 1 5 1 4 5 1 4 1 2 1 1 1 6 1 1 2 3 1 5 2 1 3 6 1 1 1 7 1 5 1 1 2 3 2 1 3 3 1 2 1 1 1 2 1 1 1 1 4 1 1 2 5 1 2 1 1 1 1 1 3 1 1 2 3 2 7 1 1 6 2 2 3 7 1 5 1 1 1 2 1 1 1 1 5 2 1 1 7 1 2 1 1 2 1 1 1 1 2 1 1 1 1 1 6 1 1 2 1 1 1 5 1 2 1 1 16 2 3 1 11 4 6 1 1 1 1 18 1 1 2 2 1 17 2 2 7 1 1 3 1 2 1 1 2 1 5 2 1 1 1 1 1 1 1 1 2 2 1 1 2 2 1 1 1 1 1 1 44 1 1 1 2 1 1 1 2 1 3 1 2 1 2 6 2 1 1 1 2 1 3 1 5 2 2 4 1 1 2 4 1 1 6 1 1 1 1 3 3 1 1 1 9 1 1 5 1 1 1 1 3 1 1 2 1 4 6 7 1 1 1 2 4 1 1 7 1 6 1 1 2 2 1 2 2 9 1 2 1 1 1 1 2 2 1 1 20 1 1 7 4 4 1 3 3 1 1 1 1 1 1 7 1 1 1 1 3 7 1 5 1 1 2 1 13 1 1 10 2 4 2 1 3 6 1 1 2 1 1 4 1 1 1 1 1 2 1 1 3 2 3 1 1 1 3 1 1 1 7 6 1 1 5 1 1 1 7 1 2 1 1 1 7 1 1 1 1 2 3 1 1 7 1 1 1 12 3 1 1 2 1 1 1 2 1 4 1 1 1 7 2 1 2 3 4 1 1 1 2 2 1 3 5 1 4 2 2 1 2 11 2 1 1 1 1 1 6 2 2 1 1 3 2 3 1 1 5 1 4 8 1 1 2 2 8 1 1 1 6 1 7 9 1 1 1 1 1 1 1 1 6 1 1 6 7 1 1 1 2 1 5